In [1]:
# datetime 지운거
import requests
import xmltodict
import json
import pandas as pd
import numpy as np
import time
from tqdm import tqdm_notebook

In [9]:
#라이브러리 임포트
import pandas as pd 
import matplotlib.pyplot as plt 
import seaborn as sns 

#그래프 사이즈 설정
plt.figure(figsize=(15, 5))

<Figure size 1500x500 with 0 Axes>

<Figure size 1500x500 with 0 Axes>

In [186]:
pd.set_option('display.max_rows', 30)

In [44]:
pd.set_option('display.max_columns', None)

In [2]:
key='VuX0QxPw7pi8mA0BngdJX%2F%2FQQvjVe5JHTwayTrbGaJC5uK80EqVNMK9lwo4RmV5e%2B6cAF6V0qtqyhoHU0SoHUA%3D%3D'

In [3]:
loc_code = {'대곡진주': 974, '보성': 981, '수원': 119, '안동': 972, '오창청주': 977, '익산전주': 702, '철원': 970, '춘천': 978, '화순광주': 973}
obs_loc_code = {'철원': 95, '춘천': 101, '수원': 119, '오창청주': 131 , '안동': 136, '익산전주': 146, '화순광주': 156, '보성': 258, '대곡진주': 192}

In [432]:
location_data = pd.read_csv('../202009121952_LSTM_Multivariate/TEST/화순능주/SURFACE_AGR_973_HR_2018_2018_2019.csv', encoding='cp949')
location_data

지점                일시  0.5M 정시 습도(%)  1.5M 정시 습도(%)  4.0M 정시 습도(%)  \
0     973   2018-01-01 0:00           87.2           80.9           80.8   
1     973   2018-01-01 1:00           86.3           81.0           82.4   
2     973   2018-01-01 2:00           85.1           79.7           81.5   
3     973   2018-01-01 3:00           92.8           87.5           87.2   
4     973   2018-01-01 4:00           95.3           92.8           90.9   
...   ...               ...            ...            ...            ...   
7373  973  2018-11-13 11:00            NaN           99.9            NaN   
7374  973  2018-11-13 12:00            NaN           62.4            NaN   
7375  973  2018-11-13 13:00            NaN           47.4            NaN   
7376  973  2018-11-13 14:00            NaN           48.8            NaN   
7377  973  2018-11-13 15:00            NaN            NaN            NaN   

      10CM 정시 토양수분(%)  20CM 정시 토양수분(%)  30CM 정시 토양수분(%)  50CM 정시 토양수분(%)  \
0                 5.9             25.7             25.5             29.2   
1                 6.0             25.7             25.5             29.2   
2                 5.9             25.7             25.5             29.2   
3                 5.9             25.7             25.5             29.2   
4                 5.9             25.6             25.5             29.2   
...               ...              ...              ...              ...   
7373             26.1             34.2             36.9             43.4   
7374             26.2             34.2             36.8             43.4   
7375             26.1             34.1             36.8             43.4   
7376             25.9             34.1             36.7             43.4   
7377              NaN              NaN              NaN              NaN   

      0.5M 정시 기온(°C)  ...  1.5M 정시 풍속(m/s)  4.0M 정시 풍속(m/s)  정시 지면온도(°C)  \
0               -1.8  ...              0.9              1.2          1.0   
1               -0.9  ...              0.9              1.4          1.1   
2               -0.9  ...              0.9              1.4          0.9   
3               -2.6  ...              0.5              0.7          0.7   
4               -3.8  ...              0.6              1.1          0.3   
...              ...  ...              ...              ...          ...   
7373             NaN  ...              NaN              NaN         14.9   
7374             NaN  ...              NaN              NaN         16.5   
7375             NaN  ...              NaN              NaN         19.2   
7376             NaN  ...              NaN              NaN         18.0   
7377             NaN  ...              NaN              NaN          NaN   

      5CM 정시 지중온도(°C)  10CM 정시 지중온도(°C)  20CM 정시 지중온도(°C)  30CM 정시 지중온도(°C)  \
0                 2.8               3.3               3.9               4.5   
1                 2.6               3.1               3.8               4.4   
2                 2.5               3.1               3.7               4.4   
3                 2.4               3.0               3.7               4.3   
4                 2.1               2.8               3.5               4.3   
...               ...               ...               ...               ...   
7373              9.9              10.1              11.6              12.4   
7374             10.9              10.7              11.5              12.4   
7375             11.9              11.5              11.6              12.3   
7376             12.8              12.2              11.8              12.3   
7377              NaN               NaN               NaN               NaN   

      정시 누적 순복사(MJ/m2)  정시 누적 전천복사(MJ/m2)  정시 누적 반사복사(MJ/m2)  
0                 4.16               6.65               2.49  
1                 0.00               0.00               0.00  
2                 0.00               0.00               0.00  
3                 0.00               0.00               0.00  
4   

In [433]:
# 데이터프레임의 칼럼명들을 리스트에 선언
data_col = location_data.columns
data_col = data_col[2:]

# ['지점'] 에서 해당 기상청지점 코드찾기
point_list=[]
for i, idx in loc_code.items():
    if location_data['지점'][0] == idx:
        point_list.append(i)
point = obs_loc_code.get(point_list[0])

# 날짜 지정하기
day = location_data['일시'][0][:10]
day = day.replace('-','')
day = int(day)
year = str(day)[:4]

In [434]:
# raw데이터에는 날짜 결측치가 있어 공백이 없는 날짜데이터를 불러다가 새로운 데이터 프레임을 만든 후 
# 해당 날짜가 겹치면 raw데이터를 새로운 df에 복사한다
sup = pd.read_csv('TEST/day.csv', encoding='cp949')

b=sup['일시'].values
replace_day=[]

for i in b:
    temp = i.replace('2014', year)
    replace_day.append(temp)

sup['일시']=replace_day

for i in data_col:
    sup[i] = None

for i in range(len(location_data)):
    print(i)
    sup.loc[sup[sup['일시'].str.contains(location_data['일시'][i])].index.values[0]][1:] = location_data.loc[i][2:]

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062
2063
2064
2065
2066
2067
2068
2069
2070
2071
2072
2073
2074
2075
2076
2077
2078
2079
2080
2081
2082
2083
2084
2085
2086
2087
2088
2089
2090
2091


3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699
3700
3701
3702
3703
3704
3705
3706
3707
3708
3709
3710
3711
3712
3713
3714
3715
3716
3717
3718
3719
3720
3721
3722
3723
3724
3725
3726
3727
3728
3729
3730
3731
3732
3733
3734
3735


5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338
5339
5340
5341
5342
5343
5344
5345
5346
5347
5348
5349
5350
5351
5352
5353
5354
5355
5356
5357
5358
5359
5360
5361
5362
5363
5364
5365
5366
5367
5368
5369
5370
5371
5372
5373
5374
5375
5376
5377
5378
5379
5380
5381
5382
5383
5384
5385
5386
5387
5388
5389
5390
5391
5392
5393
5394
5395
5396
5397
5398
5399
5400
5401
5402
5403
5404
5405
5406
5407
5408
5409
5410
5411
5412
5413
5414
5415
5416


6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931
6932
6933
6934
6935
6936
6937
6938
6939
6940
6941
6942
6943
6944
6945
6946
6947
6948
6949
6950
6951
6952
6953
6954
6955
6956
6957
6958
6959
6960
6961
6962
6963
6964
6965
6966
6967
6968
6969
6970
6971
6972
6973
6974
6975
6976
6977
6978
6979
6980
6981
6982
6983
6984
6985
6986
6987
6988
6989
6990
6991
6992
6993
6994
6995
6996
6997
6998
6999
7000
7001
7002
7003
7004
7005
7006
7007
7008
7009
7010
7011
7012
7013
7014
7015
7016
7017
7018
7019
7020
7021
7022
7023
7024
7025
7026
7027
7028
7029
7030
7031
7032
7033
7034
7035
7036
7037
7038
7039
7040
7041
7042
7043
7044
7045
7046
7047
7048
7049
7050
7051
7052
7053
7054
7055
7056
7057
7058
7059
7060
7061
7062
7063
7064
7065
7066
7067
7068
7069
7070
7071
7072
7073
7074
7075
7076
7077
7078
7079
7080
7081
7082
7083
7084
7085
7086
7087
7088
7089
7090
7091
7092
7093
7094
7095
7096
7097
7098
7099
7100
7101
7102
7103
7104
7105
7106


In [435]:
for i in range(len(sup)):
    date = sup['일시'][i]
    if len(date[10:]) == 5:
        sup['일시'][i] = date.split(' ')[0] + ' ' + '0' + date.split(' ')[1]

In [436]:
sup

일시 0.5M 정시 습도(%) 1.5M 정시 습도(%) 4.0M 정시 습도(%)  \
0     2018-01-01 00:00          87.2          80.9          80.8   
1     2018-01-01 01:00          86.3          81.0          82.4   
2     2018-01-01 02:00          85.1          79.7          81.5   
3     2018-01-01 03:00          92.8          87.5          87.2   
4     2018-01-01 04:00          95.3          92.8          90.9   
...                ...           ...           ...           ...   
8755  2018-12-31 19:00          None          None          None   
8756  2018-12-31 20:00          None          None          None   
8757  2018-12-31 21:00          None          None          None   
8758  2018-12-31 22:00          None          None          None   
8759  2018-12-31 23:00          None          None          None   

     10CM 정시 토양수분(%) 20CM 정시 토양수분(%) 30CM 정시 토양수분(%) 50CM 정시 토양수분(%)  \
0                5.9            25.7            25.5            29.2   
1                6.0            25.7            25.5            29.2   
2                5.9            25.7            25.5            29.2   
3                5.9            25.7            25.5            29.2   
4                5.9            25.6            25.5            29.2   
...              ...             ...             ...             ...   
8755            None            None            None            None   
8756            None            None            None            None   
8757            None            None            None            None   
8758            None            None            None            None   
8759            None            None            None            None   

     0.5M 정시 기온(°C) 1.5M 정시 기온(°C)  ... 1.5M 정시 풍속(m/s) 4.0M 정시 풍속(m/s)  \
0              -1.8           -2.0  ...             0.9             1.2   
1              -0.9           -1.2  ...             0.9             1.4   
2              -0.9           -1.1  ...             0.9             1.4   
3              -2.6           -2.5  ...             0.5             0.7   
4              -3.8           -3.9  ...             0.6             1.1   
...             ...            ...  ...             ...             ...   
8755           None           None  ...            None            None   
8756           None           None  ...            None            None   
8757           None           None  ...            None            None   
8758           None           None  ...            None            None   
8759           None           None  ...            None            None   

     정시 지면온도(°C) 5CM 정시 지중온도(°C) 10CM 정시 지중온도(°C) 20CM 정시 지중온도(°C)  \
0            1.0             2.8              3.3              3.9   
1            1.1             2.6              3.1              3.8   
2            0.9             2.5              3.1              3.7   
3            0.7             2.4              3.0              3.7   
4            0.3             2.1              2.8              3.5   
...          ...             ...              ...              ...   
8755        None            None             None             None   
8756        None            None             None             None   
8757        None            None             None             None   
8758        None            None             None             None   
8759        None            None             None             None   

     30CM 정시 지중온도(°C) 정시 누적 순복사(MJ/m2) 정시 누적 전천복사(MJ/m2) 정시 누적 반사복사(MJ/m2)  
0                 4.5             4.16              6.65              2.49  
1                 4.4              0.0               0.0               0.0  
2                 4.4              0.0               0.0               0.0  
3                 4.3              0.0               0.0               0.0  
4                 4.3              0.0               0.0               0.0  
...               ...              ...               ...               ...  
8755             None             None              None 

In [437]:
# 1칸만 결측치가 있을 시 앞 뒤 데이터의 평균값으로 결측치 대체
col = data_col[0]
for i in tqdm_notebook(data_col):
    for q in range(len(sup)):
        try:
            if sup[i].isnull()[q] == True:
                print(q, '--', sup['일시'][q] , '--',i)
                sup[i][q] = (sup[i][q-1] + sup[i][q+1]) / 2
        except:
            pass

C:\Users\leedo\AppData\Local\Temp\ipykernel_3120\1218708940.py:3: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  for i in tqdm_notebook(data_col):


  0%|          | 0/20 [00:00<?, ?it/s]

2099 -- 2018-03-29 11:00 -- 0.5M 정시 습도(%)
2100 -- 2018-03-29 12:00 -- 0.5M 정시 습도(%)
2101 -- 2018-03-29 13:00 -- 0.5M 정시 습도(%)
2102 -- 2018-03-29 14:00 -- 0.5M 정시 습도(%)
3990 -- 2018-06-16 06:00 -- 0.5M 정시 습도(%)
5620 -- 2018-08-23 04:00 -- 0.5M 정시 습도(%)
5621 -- 2018-08-23 05:00 -- 0.5M 정시 습도(%)
5622 -- 2018-08-23 06:00 -- 0.5M 정시 습도(%)
6725 -- 2018-10-08 05:00 -- 0.5M 정시 습도(%)
6726 -- 2018-10-08 06:00 -- 0.5M 정시 습도(%)
7235 -- 2018-10-29 11:00 -- 0.5M 정시 습도(%)
7236 -- 2018-10-29 12:00 -- 0.5M 정시 습도(%)
7237 -- 2018-10-29 13:00 -- 0.5M 정시 습도(%)
7238 -- 2018-10-29 14:00 -- 0.5M 정시 습도(%)
7239 -- 2018-10-29 15:00 -- 0.5M 정시 습도(%)
7240 -- 2018-10-29 16:00 -- 0.5M 정시 습도(%)
7241 -- 2018-10-29 17:00 -- 0.5M 정시 습도(%)
7242 -- 2018-10-29 18:00 -- 0.5M 정시 습도(%)
7243 -- 2018-10-29 19:00 -- 0.5M 정시 습도(%)
7244 -- 2018-10-29 20:00 -- 0.5M 정시 습도(%)
7245 -- 2018-10-29 21:00 -- 0.5M 정시 습도(%)
7246 -- 2018-10-29 22:00 -- 0.5M 정시 습도(%)
7247 -- 2018-10-29 23:00 -- 0.5M 정시 습도(%)
7248 -- 2018-10-30 00:00 -- 0.5M 정

7808 -- 2018-11-22 08:00 -- 0.5M 정시 습도(%)
7809 -- 2018-11-22 09:00 -- 0.5M 정시 습도(%)
7810 -- 2018-11-22 10:00 -- 0.5M 정시 습도(%)
7811 -- 2018-11-22 11:00 -- 0.5M 정시 습도(%)
7812 -- 2018-11-22 12:00 -- 0.5M 정시 습도(%)
7813 -- 2018-11-22 13:00 -- 0.5M 정시 습도(%)
7814 -- 2018-11-22 14:00 -- 0.5M 정시 습도(%)
7815 -- 2018-11-22 15:00 -- 0.5M 정시 습도(%)
7816 -- 2018-11-22 16:00 -- 0.5M 정시 습도(%)
7817 -- 2018-11-22 17:00 -- 0.5M 정시 습도(%)
7818 -- 2018-11-22 18:00 -- 0.5M 정시 습도(%)
7819 -- 2018-11-22 19:00 -- 0.5M 정시 습도(%)
7820 -- 2018-11-22 20:00 -- 0.5M 정시 습도(%)
7821 -- 2018-11-22 21:00 -- 0.5M 정시 습도(%)
7822 -- 2018-11-22 22:00 -- 0.5M 정시 습도(%)
7823 -- 2018-11-22 23:00 -- 0.5M 정시 습도(%)
7824 -- 2018-11-23 00:00 -- 0.5M 정시 습도(%)
7825 -- 2018-11-23 01:00 -- 0.5M 정시 습도(%)
7826 -- 2018-11-23 02:00 -- 0.5M 정시 습도(%)
7827 -- 2018-11-23 03:00 -- 0.5M 정시 습도(%)
7828 -- 2018-11-23 04:00 -- 0.5M 정시 습도(%)
7829 -- 2018-11-23 05:00 -- 0.5M 정시 습도(%)
7830 -- 2018-11-23 06:00 -- 0.5M 정시 습도(%)
7831 -- 2018-11-23 07:00 -- 0.5M 정

8236 -- 2018-12-10 04:00 -- 0.5M 정시 습도(%)
8237 -- 2018-12-10 05:00 -- 0.5M 정시 습도(%)
8238 -- 2018-12-10 06:00 -- 0.5M 정시 습도(%)
8239 -- 2018-12-10 07:00 -- 0.5M 정시 습도(%)
8240 -- 2018-12-10 08:00 -- 0.5M 정시 습도(%)
8241 -- 2018-12-10 09:00 -- 0.5M 정시 습도(%)
8242 -- 2018-12-10 10:00 -- 0.5M 정시 습도(%)
8243 -- 2018-12-10 11:00 -- 0.5M 정시 습도(%)
8244 -- 2018-12-10 12:00 -- 0.5M 정시 습도(%)
8245 -- 2018-12-10 13:00 -- 0.5M 정시 습도(%)
8246 -- 2018-12-10 14:00 -- 0.5M 정시 습도(%)
8247 -- 2018-12-10 15:00 -- 0.5M 정시 습도(%)
8248 -- 2018-12-10 16:00 -- 0.5M 정시 습도(%)
8249 -- 2018-12-10 17:00 -- 0.5M 정시 습도(%)
8250 -- 2018-12-10 18:00 -- 0.5M 정시 습도(%)
8251 -- 2018-12-10 19:00 -- 0.5M 정시 습도(%)
8252 -- 2018-12-10 20:00 -- 0.5M 정시 습도(%)
8253 -- 2018-12-10 21:00 -- 0.5M 정시 습도(%)
8254 -- 2018-12-10 22:00 -- 0.5M 정시 습도(%)
8255 -- 2018-12-10 23:00 -- 0.5M 정시 습도(%)
8256 -- 2018-12-11 00:00 -- 0.5M 정시 습도(%)
8257 -- 2018-12-11 01:00 -- 0.5M 정시 습도(%)
8258 -- 2018-12-11 02:00 -- 0.5M 정시 습도(%)
8259 -- 2018-12-11 03:00 -- 0.5M 정

...

8559 -- 2018-12-23 15:00 -- 정시 누적 전천복사(MJ/m2)
8560 -- 2018-12-23 16:00 -- 정시 누적 전천복사(MJ/m2)
8561 -- 2018-12-23 17:00 -- 정시 누적 전천복사(MJ/m2)
8562 -- 2018-12-23 18:00 -- 정시 누적 전천복사(MJ/m2)
8563 -- 2018-12-23 19:00 -- 정시 누적 전천복사(MJ/m2)
8564 -- 2018-12-23 20:00 -- 정시 누적 전천복사(MJ/m2)
8565 -- 2018-12-23 21:00 -- 정시 누적 전천복사(MJ/m2)
8566 -- 2018-12-23 22:00 -- 정시 누적 전천복사(MJ/m2)
8567 -- 2018-12-23 23:00 -- 정시 누적 전천복사(MJ/m2)
8568 -- 2018-12-24 00:00 -- 정시 누적 전천복사(MJ/m2)
8569 -- 2018-12-24 01:00 -- 정시 누적 전천복사(MJ/m2)
8570 -- 2018-12-24 02:00 -- 정시 누적 전천복사(MJ/m2)
8571 -- 2018-12-24 03:00 -- 정시 누적 전천복사(MJ/m2)
8572 -- 2018-12-24 04:00 -- 정시 누적 전천복사(MJ/m2)
8573 -- 2018-12-24 05:00 -- 정시 누적 전천복사(MJ/m2)
8574 -- 2018-12-24 06:00 -- 정시 누적 전천복사(MJ/m2)
8575 -- 2018-12-24 07:00 -- 정시 누적 전천복사(MJ/m2)
8576 -- 2018-12-24 08:00 -- 정시 누적 전천복사(MJ/m2)
8577 -- 2018-12-24 09:00 -- 정시 누적 전천복사(MJ/m2)
8578 -- 2018-12-24 10:00 -- 정시 누적 전천복사(MJ/m2)
8579 -- 2018-12-24 11:00 -- 정시 누적 전천복사(MJ/m2)
8580 -- 2018-12-24 12:00 -- 정시 누적 

2099 -- 2018-03-29 11:00 -- 정시 누적 반사복사(MJ/m2)
2100 -- 2018-03-29 12:00 -- 정시 누적 반사복사(MJ/m2)
2101 -- 2018-03-29 13:00 -- 정시 누적 반사복사(MJ/m2)
2102 -- 2018-03-29 14:00 -- 정시 누적 반사복사(MJ/m2)
3990 -- 2018-06-16 06:00 -- 정시 누적 반사복사(MJ/m2)
5620 -- 2018-08-23 04:00 -- 정시 누적 반사복사(MJ/m2)
5621 -- 2018-08-23 05:00 -- 정시 누적 반사복사(MJ/m2)
5622 -- 2018-08-23 06:00 -- 정시 누적 반사복사(MJ/m2)
6725 -- 2018-10-08 05:00 -- 정시 누적 반사복사(MJ/m2)
6726 -- 2018-10-08 06:00 -- 정시 누적 반사복사(MJ/m2)
7235 -- 2018-10-29 11:00 -- 정시 누적 반사복사(MJ/m2)
7236 -- 2018-10-29 12:00 -- 정시 누적 반사복사(MJ/m2)
7237 -- 2018-10-29 13:00 -- 정시 누적 반사복사(MJ/m2)
7238 -- 2018-10-29 14:00 -- 정시 누적 반사복사(MJ/m2)
7239 -- 2018-10-29 15:00 -- 정시 누적 반사복사(MJ/m2)
7240 -- 2018-10-29 16:00 -- 정시 누적 반사복사(MJ/m2)
7241 -- 2018-10-29 17:00 -- 정시 누적 반사복사(MJ/m2)
7242 -- 2018-10-29 18:00 -- 정시 누적 반사복사(MJ/m2)
7243 -- 2018-10-29 19:00 -- 정시 누적 반사복사(MJ/m2)
7244 -- 2018-10-29 20:00 -- 정시 누적 반사복사(MJ/m2)
7245 -- 2018-10-29 21:00 -- 정시 누적 반사복사(MJ/m2)
7246 -- 2018-10-29 22:00 -- 정시 누적 

7836 -- 2018-11-23 12:00 -- 정시 누적 반사복사(MJ/m2)
7837 -- 2018-11-23 13:00 -- 정시 누적 반사복사(MJ/m2)
7838 -- 2018-11-23 14:00 -- 정시 누적 반사복사(MJ/m2)
7839 -- 2018-11-23 15:00 -- 정시 누적 반사복사(MJ/m2)
7840 -- 2018-11-23 16:00 -- 정시 누적 반사복사(MJ/m2)
7841 -- 2018-11-23 17:00 -- 정시 누적 반사복사(MJ/m2)
7842 -- 2018-11-23 18:00 -- 정시 누적 반사복사(MJ/m2)
7843 -- 2018-11-23 19:00 -- 정시 누적 반사복사(MJ/m2)
7844 -- 2018-11-23 20:00 -- 정시 누적 반사복사(MJ/m2)
7845 -- 2018-11-23 21:00 -- 정시 누적 반사복사(MJ/m2)
7846 -- 2018-11-23 22:00 -- 정시 누적 반사복사(MJ/m2)
7847 -- 2018-11-23 23:00 -- 정시 누적 반사복사(MJ/m2)
7848 -- 2018-11-24 00:00 -- 정시 누적 반사복사(MJ/m2)
7849 -- 2018-11-24 01:00 -- 정시 누적 반사복사(MJ/m2)
7850 -- 2018-11-24 02:00 -- 정시 누적 반사복사(MJ/m2)
7851 -- 2018-11-24 03:00 -- 정시 누적 반사복사(MJ/m2)
7852 -- 2018-11-24 04:00 -- 정시 누적 반사복사(MJ/m2)
7853 -- 2018-11-24 05:00 -- 정시 누적 반사복사(MJ/m2)
7854 -- 2018-11-24 06:00 -- 정시 누적 반사복사(MJ/m2)
7855 -- 2018-11-24 07:00 -- 정시 누적 반사복사(MJ/m2)
7856 -- 2018-11-24 08:00 -- 정시 누적 반사복사(MJ/m2)
7857 -- 2018-11-24 09:00 -- 정시 누적 

8297 -- 2018-12-12 17:00 -- 정시 누적 반사복사(MJ/m2)
8298 -- 2018-12-12 18:00 -- 정시 누적 반사복사(MJ/m2)
8299 -- 2018-12-12 19:00 -- 정시 누적 반사복사(MJ/m2)
8300 -- 2018-12-12 20:00 -- 정시 누적 반사복사(MJ/m2)
8301 -- 2018-12-12 21:00 -- 정시 누적 반사복사(MJ/m2)
8302 -- 2018-12-12 22:00 -- 정시 누적 반사복사(MJ/m2)
8303 -- 2018-12-12 23:00 -- 정시 누적 반사복사(MJ/m2)
8304 -- 2018-12-13 00:00 -- 정시 누적 반사복사(MJ/m2)
8305 -- 2018-12-13 01:00 -- 정시 누적 반사복사(MJ/m2)
8306 -- 2018-12-13 02:00 -- 정시 누적 반사복사(MJ/m2)
8307 -- 2018-12-13 03:00 -- 정시 누적 반사복사(MJ/m2)
8308 -- 2018-12-13 04:00 -- 정시 누적 반사복사(MJ/m2)
8309 -- 2018-12-13 05:00 -- 정시 누적 반사복사(MJ/m2)
8310 -- 2018-12-13 06:00 -- 정시 누적 반사복사(MJ/m2)
8311 -- 2018-12-13 07:00 -- 정시 누적 반사복사(MJ/m2)
8312 -- 2018-12-13 08:00 -- 정시 누적 반사복사(MJ/m2)
8313 -- 2018-12-13 09:00 -- 정시 누적 반사복사(MJ/m2)
8314 -- 2018-12-13 10:00 -- 정시 누적 반사복사(MJ/m2)
8315 -- 2018-12-13 11:00 -- 정시 누적 반사복사(MJ/m2)
8316 -- 2018-12-13 12:00 -- 정시 누적 반사복사(MJ/m2)
8317 -- 2018-12-13 13:00 -- 정시 누적 반사복사(MJ/m2)
8318 -- 2018-12-13 14:00 -- 정시 누적 

8724 -- 2018-12-30 12:00 -- 정시 누적 반사복사(MJ/m2)
8725 -- 2018-12-30 13:00 -- 정시 누적 반사복사(MJ/m2)
8726 -- 2018-12-30 14:00 -- 정시 누적 반사복사(MJ/m2)
8727 -- 2018-12-30 15:00 -- 정시 누적 반사복사(MJ/m2)
8728 -- 2018-12-30 16:00 -- 정시 누적 반사복사(MJ/m2)
8729 -- 2018-12-30 17:00 -- 정시 누적 반사복사(MJ/m2)
8730 -- 2018-12-30 18:00 -- 정시 누적 반사복사(MJ/m2)
8731 -- 2018-12-30 19:00 -- 정시 누적 반사복사(MJ/m2)
8732 -- 2018-12-30 20:00 -- 정시 누적 반사복사(MJ/m2)
8733 -- 2018-12-30 21:00 -- 정시 누적 반사복사(MJ/m2)
8734 -- 2018-12-30 22:00 -- 정시 누적 반사복사(MJ/m2)
8735 -- 2018-12-30 23:00 -- 정시 누적 반사복사(MJ/m2)
8736 -- 2018-12-31 00:00 -- 정시 누적 반사복사(MJ/m2)
8737 -- 2018-12-31 01:00 -- 정시 누적 반사복사(MJ/m2)
8738 -- 2018-12-31 02:00 -- 정시 누적 반사복사(MJ/m2)
8739 -- 2018-12-31 03:00 -- 정시 누적 반사복사(MJ/m2)
8740 -- 2018-12-31 04:00 -- 정시 누적 반사복사(MJ/m2)
8741 -- 2018-12-31 05:00 -- 정시 누적 반사복사(MJ/m2)
8742 -- 2018-12-31 06:00 -- 정시 누적 반사복사(MJ/m2)
8743 -- 2018-12-31 07:00 -- 정시 누적 반사복사(MJ/m2)
8744 -- 2018-12-31 08:00 -- 정시 누적 반사복사(MJ/m2)
8745 -- 2018-12-31 09:00 -- 정시 누적 

In [438]:
# 2칸만 결측치가 있을 시 앞 뒤 데이터의 평균값으로 결측치 대체
col = data_col[0]
for i in tqdm_notebook(data_col):
    for q in range(len(sup)):
        try:
            if sup[i].isnull()[q] == True and sup[i].isnull()[q+1] == True:
                print(q, '--', sup['일시'][q] , '--',i)
                sup[i][q] = (sup[i][q-1] + sup[i][q+2]) / 2
                sup[i][q+1] = sup[i][q]
        except:
            pass

C:\Users\leedo\AppData\Local\Temp\ipykernel_3120\3914844623.py:3: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  for i in tqdm_notebook(data_col):


  0%|          | 0/20 [00:00<?, ?it/s]

2099 -- 2018-03-29 11:00 -- 0.5M 정시 습도(%)
2100 -- 2018-03-29 12:00 -- 0.5M 정시 습도(%)
2101 -- 2018-03-29 13:00 -- 0.5M 정시 습도(%)
5620 -- 2018-08-23 04:00 -- 0.5M 정시 습도(%)
5621 -- 2018-08-23 05:00 -- 0.5M 정시 습도(%)
6725 -- 2018-10-08 05:00 -- 0.5M 정시 습도(%)
7235 -- 2018-10-29 11:00 -- 0.5M 정시 습도(%)
7236 -- 2018-10-29 12:00 -- 0.5M 정시 습도(%)
7237 -- 2018-10-29 13:00 -- 0.5M 정시 습도(%)
7238 -- 2018-10-29 14:00 -- 0.5M 정시 습도(%)
7239 -- 2018-10-29 15:00 -- 0.5M 정시 습도(%)
7240 -- 2018-10-29 16:00 -- 0.5M 정시 습도(%)
7241 -- 2018-10-29 17:00 -- 0.5M 정시 습도(%)
7242 -- 2018-10-29 18:00 -- 0.5M 정시 습도(%)
7243 -- 2018-10-29 19:00 -- 0.5M 정시 습도(%)
7244 -- 2018-10-29 20:00 -- 0.5M 정시 습도(%)
7245 -- 2018-10-29 21:00 -- 0.5M 정시 습도(%)
7246 -- 2018-10-29 22:00 -- 0.5M 정시 습도(%)
7247 -- 2018-10-29 23:00 -- 0.5M 정시 습도(%)
7248 -- 2018-10-30 00:00 -- 0.5M 정시 습도(%)
7249 -- 2018-10-30 01:00 -- 0.5M 정시 습도(%)
7250 -- 2018-10-30 02:00 -- 0.5M 정시 습도(%)
7251 -- 2018-10-30 03:00 -- 0.5M 정시 습도(%)
7252 -- 2018-10-30 04:00 -- 0.5M 정

7555 -- 2018-11-11 19:00 -- 0.5M 정시 습도(%)
7556 -- 2018-11-11 20:00 -- 0.5M 정시 습도(%)
7557 -- 2018-11-11 21:00 -- 0.5M 정시 습도(%)
7558 -- 2018-11-11 22:00 -- 0.5M 정시 습도(%)
7559 -- 2018-11-11 23:00 -- 0.5M 정시 습도(%)
7560 -- 2018-11-12 00:00 -- 0.5M 정시 습도(%)
7561 -- 2018-11-12 01:00 -- 0.5M 정시 습도(%)
7562 -- 2018-11-12 02:00 -- 0.5M 정시 습도(%)
7563 -- 2018-11-12 03:00 -- 0.5M 정시 습도(%)
7564 -- 2018-11-12 04:00 -- 0.5M 정시 습도(%)
7565 -- 2018-11-12 05:00 -- 0.5M 정시 습도(%)
7566 -- 2018-11-12 06:00 -- 0.5M 정시 습도(%)
7567 -- 2018-11-12 07:00 -- 0.5M 정시 습도(%)
7568 -- 2018-11-12 08:00 -- 0.5M 정시 습도(%)
7569 -- 2018-11-12 09:00 -- 0.5M 정시 습도(%)
7570 -- 2018-11-12 10:00 -- 0.5M 정시 습도(%)
7571 -- 2018-11-12 11:00 -- 0.5M 정시 습도(%)
7572 -- 2018-11-12 12:00 -- 0.5M 정시 습도(%)
7573 -- 2018-11-12 13:00 -- 0.5M 정시 습도(%)
7574 -- 2018-11-12 14:00 -- 0.5M 정시 습도(%)
7575 -- 2018-11-12 15:00 -- 0.5M 정시 습도(%)
7576 -- 2018-11-12 16:00 -- 0.5M 정시 습도(%)
7577 -- 2018-11-12 17:00 -- 0.5M 정시 습도(%)
7578 -- 2018-11-12 18:00 -- 0.5M 정

7767 -- 2018-11-20 15:00 -- 0.5M 정시 습도(%)
7768 -- 2018-11-20 16:00 -- 0.5M 정시 습도(%)
7769 -- 2018-11-20 17:00 -- 0.5M 정시 습도(%)
7770 -- 2018-11-20 18:00 -- 0.5M 정시 습도(%)
7771 -- 2018-11-20 19:00 -- 0.5M 정시 습도(%)
7772 -- 2018-11-20 20:00 -- 0.5M 정시 습도(%)
7773 -- 2018-11-20 21:00 -- 0.5M 정시 습도(%)
7774 -- 2018-11-20 22:00 -- 0.5M 정시 습도(%)
7775 -- 2018-11-20 23:00 -- 0.5M 정시 습도(%)
7776 -- 2018-11-21 00:00 -- 0.5M 정시 습도(%)
7777 -- 2018-11-21 01:00 -- 0.5M 정시 습도(%)
7778 -- 2018-11-21 02:00 -- 0.5M 정시 습도(%)
7779 -- 2018-11-21 03:00 -- 0.5M 정시 습도(%)
7780 -- 2018-11-21 04:00 -- 0.5M 정시 습도(%)
7781 -- 2018-11-21 05:00 -- 0.5M 정시 습도(%)
7782 -- 2018-11-21 06:00 -- 0.5M 정시 습도(%)
7783 -- 2018-11-21 07:00 -- 0.5M 정시 습도(%)
7784 -- 2018-11-21 08:00 -- 0.5M 정시 습도(%)
7785 -- 2018-11-21 09:00 -- 0.5M 정시 습도(%)
7786 -- 2018-11-21 10:00 -- 0.5M 정시 습도(%)
7787 -- 2018-11-21 11:00 -- 0.5M 정시 습도(%)
7788 -- 2018-11-21 12:00 -- 0.5M 정시 습도(%)
7789 -- 2018-11-21 13:00 -- 0.5M 정시 습도(%)
7790 -- 2018-11-21 14:00 -- 0.5M 정

...

7551 -- 2018-11-11 15:00 -- 정시 누적 반사복사(MJ/m2)
7552 -- 2018-11-11 16:00 -- 정시 누적 반사복사(MJ/m2)
7553 -- 2018-11-11 17:00 -- 정시 누적 반사복사(MJ/m2)
7554 -- 2018-11-11 18:00 -- 정시 누적 반사복사(MJ/m2)
7555 -- 2018-11-11 19:00 -- 정시 누적 반사복사(MJ/m2)
7556 -- 2018-11-11 20:00 -- 정시 누적 반사복사(MJ/m2)
7557 -- 2018-11-11 21:00 -- 정시 누적 반사복사(MJ/m2)
7558 -- 2018-11-11 22:00 -- 정시 누적 반사복사(MJ/m2)
7559 -- 2018-11-11 23:00 -- 정시 누적 반사복사(MJ/m2)
7560 -- 2018-11-12 00:00 -- 정시 누적 반사복사(MJ/m2)
7561 -- 2018-11-12 01:00 -- 정시 누적 반사복사(MJ/m2)
7562 -- 2018-11-12 02:00 -- 정시 누적 반사복사(MJ/m2)
7563 -- 2018-11-12 03:00 -- 정시 누적 반사복사(MJ/m2)
7564 -- 2018-11-12 04:00 -- 정시 누적 반사복사(MJ/m2)
7565 -- 2018-11-12 05:00 -- 정시 누적 반사복사(MJ/m2)
7566 -- 2018-11-12 06:00 -- 정시 누적 반사복사(MJ/m2)
7567 -- 2018-11-12 07:00 -- 정시 누적 반사복사(MJ/m2)
7568 -- 2018-11-12 08:00 -- 정시 누적 반사복사(MJ/m2)
7569 -- 2018-11-12 09:00 -- 정시 누적 반사복사(MJ/m2)
7570 -- 2018-11-12 10:00 -- 정시 누적 반사복사(MJ/m2)
7571 -- 2018-11-12 11:00 -- 정시 누적 반사복사(MJ/m2)
7572 -- 2018-11-12 12:00 -- 정시 누적 

7756 -- 2018-11-20 04:00 -- 정시 누적 반사복사(MJ/m2)
7757 -- 2018-11-20 05:00 -- 정시 누적 반사복사(MJ/m2)
7758 -- 2018-11-20 06:00 -- 정시 누적 반사복사(MJ/m2)
7759 -- 2018-11-20 07:00 -- 정시 누적 반사복사(MJ/m2)
7760 -- 2018-11-20 08:00 -- 정시 누적 반사복사(MJ/m2)
7761 -- 2018-11-20 09:00 -- 정시 누적 반사복사(MJ/m2)
7762 -- 2018-11-20 10:00 -- 정시 누적 반사복사(MJ/m2)
7763 -- 2018-11-20 11:00 -- 정시 누적 반사복사(MJ/m2)
7764 -- 2018-11-20 12:00 -- 정시 누적 반사복사(MJ/m2)
7765 -- 2018-11-20 13:00 -- 정시 누적 반사복사(MJ/m2)
7766 -- 2018-11-20 14:00 -- 정시 누적 반사복사(MJ/m2)
7767 -- 2018-11-20 15:00 -- 정시 누적 반사복사(MJ/m2)
7768 -- 2018-11-20 16:00 -- 정시 누적 반사복사(MJ/m2)
7769 -- 2018-11-20 17:00 -- 정시 누적 반사복사(MJ/m2)
7770 -- 2018-11-20 18:00 -- 정시 누적 반사복사(MJ/m2)
7771 -- 2018-11-20 19:00 -- 정시 누적 반사복사(MJ/m2)
7772 -- 2018-11-20 20:00 -- 정시 누적 반사복사(MJ/m2)
7773 -- 2018-11-20 21:00 -- 정시 누적 반사복사(MJ/m2)
7774 -- 2018-11-20 22:00 -- 정시 누적 반사복사(MJ/m2)
7775 -- 2018-11-20 23:00 -- 정시 누적 반사복사(MJ/m2)
7776 -- 2018-11-21 00:00 -- 정시 누적 반사복사(MJ/m2)
7777 -- 2018-11-21 01:00 -- 정시 누적 

8108 -- 2018-12-04 20:00 -- 정시 누적 반사복사(MJ/m2)
8109 -- 2018-12-04 21:00 -- 정시 누적 반사복사(MJ/m2)
8110 -- 2018-12-04 22:00 -- 정시 누적 반사복사(MJ/m2)
8111 -- 2018-12-04 23:00 -- 정시 누적 반사복사(MJ/m2)
8112 -- 2018-12-05 00:00 -- 정시 누적 반사복사(MJ/m2)
8113 -- 2018-12-05 01:00 -- 정시 누적 반사복사(MJ/m2)
8114 -- 2018-12-05 02:00 -- 정시 누적 반사복사(MJ/m2)
8115 -- 2018-12-05 03:00 -- 정시 누적 반사복사(MJ/m2)
8116 -- 2018-12-05 04:00 -- 정시 누적 반사복사(MJ/m2)
8117 -- 2018-12-05 05:00 -- 정시 누적 반사복사(MJ/m2)
8118 -- 2018-12-05 06:00 -- 정시 누적 반사복사(MJ/m2)
8119 -- 2018-12-05 07:00 -- 정시 누적 반사복사(MJ/m2)
8120 -- 2018-12-05 08:00 -- 정시 누적 반사복사(MJ/m2)
8121 -- 2018-12-05 09:00 -- 정시 누적 반사복사(MJ/m2)
8122 -- 2018-12-05 10:00 -- 정시 누적 반사복사(MJ/m2)
8123 -- 2018-12-05 11:00 -- 정시 누적 반사복사(MJ/m2)
8124 -- 2018-12-05 12:00 -- 정시 누적 반사복사(MJ/m2)
8125 -- 2018-12-05 13:00 -- 정시 누적 반사복사(MJ/m2)
8126 -- 2018-12-05 14:00 -- 정시 누적 반사복사(MJ/m2)
8127 -- 2018-12-05 15:00 -- 정시 누적 반사복사(MJ/m2)
8128 -- 2018-12-05 16:00 -- 정시 누적 반사복사(MJ/m2)
8129 -- 2018-12-05 17:00 -- 정시 누적 

8346 -- 2018-12-14 18:00 -- 정시 누적 반사복사(MJ/m2)
8347 -- 2018-12-14 19:00 -- 정시 누적 반사복사(MJ/m2)
8348 -- 2018-12-14 20:00 -- 정시 누적 반사복사(MJ/m2)
8349 -- 2018-12-14 21:00 -- 정시 누적 반사복사(MJ/m2)
8350 -- 2018-12-14 22:00 -- 정시 누적 반사복사(MJ/m2)
8351 -- 2018-12-14 23:00 -- 정시 누적 반사복사(MJ/m2)
8352 -- 2018-12-15 00:00 -- 정시 누적 반사복사(MJ/m2)
8353 -- 2018-12-15 01:00 -- 정시 누적 반사복사(MJ/m2)
8354 -- 2018-12-15 02:00 -- 정시 누적 반사복사(MJ/m2)
8355 -- 2018-12-15 03:00 -- 정시 누적 반사복사(MJ/m2)
8356 -- 2018-12-15 04:00 -- 정시 누적 반사복사(MJ/m2)
8357 -- 2018-12-15 05:00 -- 정시 누적 반사복사(MJ/m2)
8358 -- 2018-12-15 06:00 -- 정시 누적 반사복사(MJ/m2)
8359 -- 2018-12-15 07:00 -- 정시 누적 반사복사(MJ/m2)
8360 -- 2018-12-15 08:00 -- 정시 누적 반사복사(MJ/m2)
8361 -- 2018-12-15 09:00 -- 정시 누적 반사복사(MJ/m2)
8362 -- 2018-12-15 10:00 -- 정시 누적 반사복사(MJ/m2)
8363 -- 2018-12-15 11:00 -- 정시 누적 반사복사(MJ/m2)
8364 -- 2018-12-15 12:00 -- 정시 누적 반사복사(MJ/m2)
8365 -- 2018-12-15 13:00 -- 정시 누적 반사복사(MJ/m2)
8366 -- 2018-12-15 14:00 -- 정시 누적 반사복사(MJ/m2)
8367 -- 2018-12-15 15:00 -- 정시 누적 

8593 -- 2018-12-25 01:00 -- 정시 누적 반사복사(MJ/m2)
8594 -- 2018-12-25 02:00 -- 정시 누적 반사복사(MJ/m2)
8595 -- 2018-12-25 03:00 -- 정시 누적 반사복사(MJ/m2)
8596 -- 2018-12-25 04:00 -- 정시 누적 반사복사(MJ/m2)
8597 -- 2018-12-25 05:00 -- 정시 누적 반사복사(MJ/m2)
8598 -- 2018-12-25 06:00 -- 정시 누적 반사복사(MJ/m2)
8599 -- 2018-12-25 07:00 -- 정시 누적 반사복사(MJ/m2)
8600 -- 2018-12-25 08:00 -- 정시 누적 반사복사(MJ/m2)
8601 -- 2018-12-25 09:00 -- 정시 누적 반사복사(MJ/m2)
8602 -- 2018-12-25 10:00 -- 정시 누적 반사복사(MJ/m2)
8603 -- 2018-12-25 11:00 -- 정시 누적 반사복사(MJ/m2)
8604 -- 2018-12-25 12:00 -- 정시 누적 반사복사(MJ/m2)
8605 -- 2018-12-25 13:00 -- 정시 누적 반사복사(MJ/m2)
8606 -- 2018-12-25 14:00 -- 정시 누적 반사복사(MJ/m2)
8607 -- 2018-12-25 15:00 -- 정시 누적 반사복사(MJ/m2)
8608 -- 2018-12-25 16:00 -- 정시 누적 반사복사(MJ/m2)
8609 -- 2018-12-25 17:00 -- 정시 누적 반사복사(MJ/m2)
8610 -- 2018-12-25 18:00 -- 정시 누적 반사복사(MJ/m2)
8611 -- 2018-12-25 19:00 -- 정시 누적 반사복사(MJ/m2)
8612 -- 2018-12-25 20:00 -- 정시 누적 반사복사(MJ/m2)
8613 -- 2018-12-25 21:00 -- 정시 누적 반사복사(MJ/m2)
8614 -- 2018-12-25 22:00 -- 정시 누적 

In [439]:
# 3칸만 결측치가 있을 시 앞 뒤 데이터의 평균값으로 결측치 대체
col = data_col[0]
for i in tqdm_notebook(data_col):
    for q in range(len(sup)):
        try:
            if sup[i].isnull()[q] == True and sup[i].isnull()[q+1] == True and sup[i].isnull()[q+2] == True:
                print(q, '--', sup['일시'][q] , '--',i)
                sup[i][q] = (sup[i][q-1] + sup[i][q+3]) / 2
                sup[i][q+1] = sup[i][q]
                sup[i][q+2] = sup[i][q]
        except:
            pass

C:\Users\leedo\AppData\Local\Temp\ipykernel_3120\3478952892.py:3: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  for i in tqdm_notebook(data_col):


  0%|          | 0/20 [00:00<?, ?it/s]

2099 -- 2018-03-29 11:00 -- 0.5M 정시 습도(%)
2100 -- 2018-03-29 12:00 -- 0.5M 정시 습도(%)
5620 -- 2018-08-23 04:00 -- 0.5M 정시 습도(%)
7235 -- 2018-10-29 11:00 -- 0.5M 정시 습도(%)
7236 -- 2018-10-29 12:00 -- 0.5M 정시 습도(%)
7237 -- 2018-10-29 13:00 -- 0.5M 정시 습도(%)
7238 -- 2018-10-29 14:00 -- 0.5M 정시 습도(%)
7239 -- 2018-10-29 15:00 -- 0.5M 정시 습도(%)
7240 -- 2018-10-29 16:00 -- 0.5M 정시 습도(%)
7241 -- 2018-10-29 17:00 -- 0.5M 정시 습도(%)
7242 -- 2018-10-29 18:00 -- 0.5M 정시 습도(%)
7243 -- 2018-10-29 19:00 -- 0.5M 정시 습도(%)
7244 -- 2018-10-29 20:00 -- 0.5M 정시 습도(%)
7245 -- 2018-10-29 21:00 -- 0.5M 정시 습도(%)
7246 -- 2018-10-29 22:00 -- 0.5M 정시 습도(%)
7247 -- 2018-10-29 23:00 -- 0.5M 정시 습도(%)
7248 -- 2018-10-30 00:00 -- 0.5M 정시 습도(%)
7249 -- 2018-10-30 01:00 -- 0.5M 정시 습도(%)
7250 -- 2018-10-30 02:00 -- 0.5M 정시 습도(%)
7251 -- 2018-10-30 03:00 -- 0.5M 정시 습도(%)
7252 -- 2018-10-30 04:00 -- 0.5M 정시 습도(%)
7253 -- 2018-10-30 05:00 -- 0.5M 정시 습도(%)
7254 -- 2018-10-30 06:00 -- 0.5M 정시 습도(%)
7255 -- 2018-10-30 07:00 -- 0.5M 정

7566 -- 2018-11-12 06:00 -- 0.5M 정시 습도(%)
7567 -- 2018-11-12 07:00 -- 0.5M 정시 습도(%)
7568 -- 2018-11-12 08:00 -- 0.5M 정시 습도(%)
7569 -- 2018-11-12 09:00 -- 0.5M 정시 습도(%)
7570 -- 2018-11-12 10:00 -- 0.5M 정시 습도(%)
7571 -- 2018-11-12 11:00 -- 0.5M 정시 습도(%)
7572 -- 2018-11-12 12:00 -- 0.5M 정시 습도(%)
7573 -- 2018-11-12 13:00 -- 0.5M 정시 습도(%)
7574 -- 2018-11-12 14:00 -- 0.5M 정시 습도(%)
7575 -- 2018-11-12 15:00 -- 0.5M 정시 습도(%)
7576 -- 2018-11-12 16:00 -- 0.5M 정시 습도(%)
7577 -- 2018-11-12 17:00 -- 0.5M 정시 습도(%)
7578 -- 2018-11-12 18:00 -- 0.5M 정시 습도(%)
7579 -- 2018-11-12 19:00 -- 0.5M 정시 습도(%)
7580 -- 2018-11-12 20:00 -- 0.5M 정시 습도(%)
7581 -- 2018-11-12 21:00 -- 0.5M 정시 습도(%)
7582 -- 2018-11-12 22:00 -- 0.5M 정시 습도(%)
7583 -- 2018-11-12 23:00 -- 0.5M 정시 습도(%)
7584 -- 2018-11-13 00:00 -- 0.5M 정시 습도(%)
7585 -- 2018-11-13 01:00 -- 0.5M 정시 습도(%)
7586 -- 2018-11-13 02:00 -- 0.5M 정시 습도(%)
7587 -- 2018-11-13 03:00 -- 0.5M 정시 습도(%)
7588 -- 2018-11-13 04:00 -- 0.5M 정시 습도(%)
7589 -- 2018-11-13 05:00 -- 0.5M 정

7941 -- 2018-11-27 21:00 -- 0.5M 정시 습도(%)
7942 -- 2018-11-27 22:00 -- 0.5M 정시 습도(%)
7943 -- 2018-11-27 23:00 -- 0.5M 정시 습도(%)
7944 -- 2018-11-28 00:00 -- 0.5M 정시 습도(%)
7945 -- 2018-11-28 01:00 -- 0.5M 정시 습도(%)
7946 -- 2018-11-28 02:00 -- 0.5M 정시 습도(%)
7947 -- 2018-11-28 03:00 -- 0.5M 정시 습도(%)
7948 -- 2018-11-28 04:00 -- 0.5M 정시 습도(%)
7949 -- 2018-11-28 05:00 -- 0.5M 정시 습도(%)
7950 -- 2018-11-28 06:00 -- 0.5M 정시 습도(%)
7951 -- 2018-11-28 07:00 -- 0.5M 정시 습도(%)
7952 -- 2018-11-28 08:00 -- 0.5M 정시 습도(%)
7953 -- 2018-11-28 09:00 -- 0.5M 정시 습도(%)
7954 -- 2018-11-28 10:00 -- 0.5M 정시 습도(%)
7955 -- 2018-11-28 11:00 -- 0.5M 정시 습도(%)
7956 -- 2018-11-28 12:00 -- 0.5M 정시 습도(%)
7957 -- 2018-11-28 13:00 -- 0.5M 정시 습도(%)
7958 -- 2018-11-28 14:00 -- 0.5M 정시 습도(%)
7959 -- 2018-11-28 15:00 -- 0.5M 정시 습도(%)
7960 -- 2018-11-28 16:00 -- 0.5M 정시 습도(%)
7961 -- 2018-11-28 17:00 -- 0.5M 정시 습도(%)
7962 -- 2018-11-28 18:00 -- 0.5M 정시 습도(%)
7963 -- 2018-11-28 19:00 -- 0.5M 정시 습도(%)
7964 -- 2018-11-28 20:00 -- 0.5M 정

...

7391 -- 2018-11-04 23:00 -- 정시 누적 반사복사(MJ/m2)
7392 -- 2018-11-05 00:00 -- 정시 누적 반사복사(MJ/m2)
7393 -- 2018-11-05 01:00 -- 정시 누적 반사복사(MJ/m2)
7394 -- 2018-11-05 02:00 -- 정시 누적 반사복사(MJ/m2)
7395 -- 2018-11-05 03:00 -- 정시 누적 반사복사(MJ/m2)
7396 -- 2018-11-05 04:00 -- 정시 누적 반사복사(MJ/m2)
7397 -- 2018-11-05 05:00 -- 정시 누적 반사복사(MJ/m2)
7398 -- 2018-11-05 06:00 -- 정시 누적 반사복사(MJ/m2)
7399 -- 2018-11-05 07:00 -- 정시 누적 반사복사(MJ/m2)
7400 -- 2018-11-05 08:00 -- 정시 누적 반사복사(MJ/m2)
7401 -- 2018-11-05 09:00 -- 정시 누적 반사복사(MJ/m2)
7402 -- 2018-11-05 10:00 -- 정시 누적 반사복사(MJ/m2)
7403 -- 2018-11-05 11:00 -- 정시 누적 반사복사(MJ/m2)
7404 -- 2018-11-05 12:00 -- 정시 누적 반사복사(MJ/m2)
7405 -- 2018-11-05 13:00 -- 정시 누적 반사복사(MJ/m2)
7406 -- 2018-11-05 14:00 -- 정시 누적 반사복사(MJ/m2)
7407 -- 2018-11-05 15:00 -- 정시 누적 반사복사(MJ/m2)
7408 -- 2018-11-05 16:00 -- 정시 누적 반사복사(MJ/m2)
7409 -- 2018-11-05 17:00 -- 정시 누적 반사복사(MJ/m2)
7410 -- 2018-11-05 18:00 -- 정시 누적 반사복사(MJ/m2)
7411 -- 2018-11-05 19:00 -- 정시 누적 반사복사(MJ/m2)
7412 -- 2018-11-05 20:00 -- 정시 누적 

7579 -- 2018-11-12 19:00 -- 정시 누적 반사복사(MJ/m2)
7580 -- 2018-11-12 20:00 -- 정시 누적 반사복사(MJ/m2)
7581 -- 2018-11-12 21:00 -- 정시 누적 반사복사(MJ/m2)
7582 -- 2018-11-12 22:00 -- 정시 누적 반사복사(MJ/m2)
7583 -- 2018-11-12 23:00 -- 정시 누적 반사복사(MJ/m2)
7584 -- 2018-11-13 00:00 -- 정시 누적 반사복사(MJ/m2)
7585 -- 2018-11-13 01:00 -- 정시 누적 반사복사(MJ/m2)
7586 -- 2018-11-13 02:00 -- 정시 누적 반사복사(MJ/m2)
7587 -- 2018-11-13 03:00 -- 정시 누적 반사복사(MJ/m2)
7588 -- 2018-11-13 04:00 -- 정시 누적 반사복사(MJ/m2)
7589 -- 2018-11-13 05:00 -- 정시 누적 반사복사(MJ/m2)
7590 -- 2018-11-13 06:00 -- 정시 누적 반사복사(MJ/m2)
7591 -- 2018-11-13 07:00 -- 정시 누적 반사복사(MJ/m2)
7592 -- 2018-11-13 08:00 -- 정시 누적 반사복사(MJ/m2)
7593 -- 2018-11-13 09:00 -- 정시 누적 반사복사(MJ/m2)
7594 -- 2018-11-13 10:00 -- 정시 누적 반사복사(MJ/m2)
7595 -- 2018-11-13 11:00 -- 정시 누적 반사복사(MJ/m2)
7596 -- 2018-11-13 12:00 -- 정시 누적 반사복사(MJ/m2)
7597 -- 2018-11-13 13:00 -- 정시 누적 반사복사(MJ/m2)
7598 -- 2018-11-13 14:00 -- 정시 누적 반사복사(MJ/m2)
7599 -- 2018-11-13 15:00 -- 정시 누적 반사복사(MJ/m2)
7600 -- 2018-11-13 16:00 -- 정시 누적 

7894 -- 2018-11-25 22:00 -- 정시 누적 반사복사(MJ/m2)
7895 -- 2018-11-25 23:00 -- 정시 누적 반사복사(MJ/m2)
7896 -- 2018-11-26 00:00 -- 정시 누적 반사복사(MJ/m2)
7897 -- 2018-11-26 01:00 -- 정시 누적 반사복사(MJ/m2)
7898 -- 2018-11-26 02:00 -- 정시 누적 반사복사(MJ/m2)
7899 -- 2018-11-26 03:00 -- 정시 누적 반사복사(MJ/m2)
7900 -- 2018-11-26 04:00 -- 정시 누적 반사복사(MJ/m2)
7901 -- 2018-11-26 05:00 -- 정시 누적 반사복사(MJ/m2)
7902 -- 2018-11-26 06:00 -- 정시 누적 반사복사(MJ/m2)
7903 -- 2018-11-26 07:00 -- 정시 누적 반사복사(MJ/m2)
7904 -- 2018-11-26 08:00 -- 정시 누적 반사복사(MJ/m2)
7905 -- 2018-11-26 09:00 -- 정시 누적 반사복사(MJ/m2)
7906 -- 2018-11-26 10:00 -- 정시 누적 반사복사(MJ/m2)
7907 -- 2018-11-26 11:00 -- 정시 누적 반사복사(MJ/m2)
7908 -- 2018-11-26 12:00 -- 정시 누적 반사복사(MJ/m2)
7909 -- 2018-11-26 13:00 -- 정시 누적 반사복사(MJ/m2)
7910 -- 2018-11-26 14:00 -- 정시 누적 반사복사(MJ/m2)
7911 -- 2018-11-26 15:00 -- 정시 누적 반사복사(MJ/m2)
7912 -- 2018-11-26 16:00 -- 정시 누적 반사복사(MJ/m2)
7913 -- 2018-11-26 17:00 -- 정시 누적 반사복사(MJ/m2)
7914 -- 2018-11-26 18:00 -- 정시 누적 반사복사(MJ/m2)
7915 -- 2018-11-26 19:00 -- 정시 누적 

8297 -- 2018-12-12 17:00 -- 정시 누적 반사복사(MJ/m2)
8298 -- 2018-12-12 18:00 -- 정시 누적 반사복사(MJ/m2)
8299 -- 2018-12-12 19:00 -- 정시 누적 반사복사(MJ/m2)
8300 -- 2018-12-12 20:00 -- 정시 누적 반사복사(MJ/m2)
8301 -- 2018-12-12 21:00 -- 정시 누적 반사복사(MJ/m2)
8302 -- 2018-12-12 22:00 -- 정시 누적 반사복사(MJ/m2)
8303 -- 2018-12-12 23:00 -- 정시 누적 반사복사(MJ/m2)
8304 -- 2018-12-13 00:00 -- 정시 누적 반사복사(MJ/m2)
8305 -- 2018-12-13 01:00 -- 정시 누적 반사복사(MJ/m2)
8306 -- 2018-12-13 02:00 -- 정시 누적 반사복사(MJ/m2)
8307 -- 2018-12-13 03:00 -- 정시 누적 반사복사(MJ/m2)
8308 -- 2018-12-13 04:00 -- 정시 누적 반사복사(MJ/m2)
8309 -- 2018-12-13 05:00 -- 정시 누적 반사복사(MJ/m2)
8310 -- 2018-12-13 06:00 -- 정시 누적 반사복사(MJ/m2)
8311 -- 2018-12-13 07:00 -- 정시 누적 반사복사(MJ/m2)
8312 -- 2018-12-13 08:00 -- 정시 누적 반사복사(MJ/m2)
8313 -- 2018-12-13 09:00 -- 정시 누적 반사복사(MJ/m2)
8314 -- 2018-12-13 10:00 -- 정시 누적 반사복사(MJ/m2)
8315 -- 2018-12-13 11:00 -- 정시 누적 반사복사(MJ/m2)
8316 -- 2018-12-13 12:00 -- 정시 누적 반사복사(MJ/m2)
8317 -- 2018-12-13 13:00 -- 정시 누적 반사복사(MJ/m2)
8318 -- 2018-12-13 14:00 -- 정시 누적 

8645 -- 2018-12-27 05:00 -- 정시 누적 반사복사(MJ/m2)
8646 -- 2018-12-27 06:00 -- 정시 누적 반사복사(MJ/m2)
8647 -- 2018-12-27 07:00 -- 정시 누적 반사복사(MJ/m2)
8648 -- 2018-12-27 08:00 -- 정시 누적 반사복사(MJ/m2)
8649 -- 2018-12-27 09:00 -- 정시 누적 반사복사(MJ/m2)
8650 -- 2018-12-27 10:00 -- 정시 누적 반사복사(MJ/m2)
8651 -- 2018-12-27 11:00 -- 정시 누적 반사복사(MJ/m2)
8652 -- 2018-12-27 12:00 -- 정시 누적 반사복사(MJ/m2)
8653 -- 2018-12-27 13:00 -- 정시 누적 반사복사(MJ/m2)
8654 -- 2018-12-27 14:00 -- 정시 누적 반사복사(MJ/m2)
8655 -- 2018-12-27 15:00 -- 정시 누적 반사복사(MJ/m2)
8656 -- 2018-12-27 16:00 -- 정시 누적 반사복사(MJ/m2)
8657 -- 2018-12-27 17:00 -- 정시 누적 반사복사(MJ/m2)
8658 -- 2018-12-27 18:00 -- 정시 누적 반사복사(MJ/m2)
8659 -- 2018-12-27 19:00 -- 정시 누적 반사복사(MJ/m2)
8660 -- 2018-12-27 20:00 -- 정시 누적 반사복사(MJ/m2)
8661 -- 2018-12-27 21:00 -- 정시 누적 반사복사(MJ/m2)
8662 -- 2018-12-27 22:00 -- 정시 누적 반사복사(MJ/m2)
8663 -- 2018-12-27 23:00 -- 정시 누적 반사복사(MJ/m2)
8664 -- 2018-12-28 00:00 -- 정시 누적 반사복사(MJ/m2)
8665 -- 2018-12-28 01:00 -- 정시 누적 반사복사(MJ/m2)
8666 -- 2018-12-28 02:00 -- 정시 누적 

In [440]:
# 4칸만 결측치가 있을 시 앞 뒤 데이터의 평균값으로 결측치 대체
col = data_col[0]
for i in tqdm_notebook(data_col):
    for q in range(len(sup)):
        try:
            if sup[i].isnull()[q] == True and sup[i].isnull()[q+1] == True and sup[i].isnull()[q+2] == True and sup[i].isnull()[q+3] == True :
                print(q, '--', sup['일시'][q] , '--',i)
                sup[i][q] = (sup[i][q-1] + sup[i][q+4]) / 2
                sup[i][q+1] = sup[i][q]
                sup[i][q+2] = sup[i][q]
                sup[i][q+3] = sup[i][q]
        except:
            pass

C:\Users\leedo\AppData\Local\Temp\ipykernel_3120\903251659.py:3: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  for i in tqdm_notebook(data_col):


  0%|          | 0/20 [00:00<?, ?it/s]

2099 -- 2018-03-29 11:00 -- 0.5M 정시 습도(%)
7235 -- 2018-10-29 11:00 -- 0.5M 정시 습도(%)
7236 -- 2018-10-29 12:00 -- 0.5M 정시 습도(%)
7237 -- 2018-10-29 13:00 -- 0.5M 정시 습도(%)
7238 -- 2018-10-29 14:00 -- 0.5M 정시 습도(%)
7239 -- 2018-10-29 15:00 -- 0.5M 정시 습도(%)
7240 -- 2018-10-29 16:00 -- 0.5M 정시 습도(%)
7241 -- 2018-10-29 17:00 -- 0.5M 정시 습도(%)
7242 -- 2018-10-29 18:00 -- 0.5M 정시 습도(%)
7243 -- 2018-10-29 19:00 -- 0.5M 정시 습도(%)
7244 -- 2018-10-29 20:00 -- 0.5M 정시 습도(%)
7245 -- 2018-10-29 21:00 -- 0.5M 정시 습도(%)
7246 -- 2018-10-29 22:00 -- 0.5M 정시 습도(%)
7247 -- 2018-10-29 23:00 -- 0.5M 정시 습도(%)
7248 -- 2018-10-30 00:00 -- 0.5M 정시 습도(%)
7249 -- 2018-10-30 01:00 -- 0.5M 정시 습도(%)
7250 -- 2018-10-30 02:00 -- 0.5M 정시 습도(%)
7251 -- 2018-10-30 03:00 -- 0.5M 정시 습도(%)
7252 -- 2018-10-30 04:00 -- 0.5M 정시 습도(%)
7253 -- 2018-10-30 05:00 -- 0.5M 정시 습도(%)
7254 -- 2018-10-30 06:00 -- 0.5M 정시 습도(%)
7255 -- 2018-10-30 07:00 -- 0.5M 정시 습도(%)
7256 -- 2018-10-30 08:00 -- 0.5M 정시 습도(%)
7257 -- 2018-10-30 09:00 -- 0.5M 정

7466 -- 2018-11-08 02:00 -- 0.5M 정시 습도(%)
7467 -- 2018-11-08 03:00 -- 0.5M 정시 습도(%)
7468 -- 2018-11-08 04:00 -- 0.5M 정시 습도(%)
7469 -- 2018-11-08 05:00 -- 0.5M 정시 습도(%)
7470 -- 2018-11-08 06:00 -- 0.5M 정시 습도(%)
7471 -- 2018-11-08 07:00 -- 0.5M 정시 습도(%)
7472 -- 2018-11-08 08:00 -- 0.5M 정시 습도(%)
7473 -- 2018-11-08 09:00 -- 0.5M 정시 습도(%)
7474 -- 2018-11-08 10:00 -- 0.5M 정시 습도(%)
7475 -- 2018-11-08 11:00 -- 0.5M 정시 습도(%)
7476 -- 2018-11-08 12:00 -- 0.5M 정시 습도(%)
7477 -- 2018-11-08 13:00 -- 0.5M 정시 습도(%)
7478 -- 2018-11-08 14:00 -- 0.5M 정시 습도(%)
7479 -- 2018-11-08 15:00 -- 0.5M 정시 습도(%)
7480 -- 2018-11-08 16:00 -- 0.5M 정시 습도(%)
7481 -- 2018-11-08 17:00 -- 0.5M 정시 습도(%)
7482 -- 2018-11-08 18:00 -- 0.5M 정시 습도(%)
7483 -- 2018-11-08 19:00 -- 0.5M 정시 습도(%)
7484 -- 2018-11-08 20:00 -- 0.5M 정시 습도(%)
7485 -- 2018-11-08 21:00 -- 0.5M 정시 습도(%)
7486 -- 2018-11-08 22:00 -- 0.5M 정시 습도(%)
7487 -- 2018-11-08 23:00 -- 0.5M 정시 습도(%)
7488 -- 2018-11-09 00:00 -- 0.5M 정시 습도(%)
7489 -- 2018-11-09 01:00 -- 0.5M 정

7671 -- 2018-11-16 15:00 -- 0.5M 정시 습도(%)
7672 -- 2018-11-16 16:00 -- 0.5M 정시 습도(%)
7673 -- 2018-11-16 17:00 -- 0.5M 정시 습도(%)
7674 -- 2018-11-16 18:00 -- 0.5M 정시 습도(%)
7675 -- 2018-11-16 19:00 -- 0.5M 정시 습도(%)
7676 -- 2018-11-16 20:00 -- 0.5M 정시 습도(%)
7677 -- 2018-11-16 21:00 -- 0.5M 정시 습도(%)
7678 -- 2018-11-16 22:00 -- 0.5M 정시 습도(%)
7679 -- 2018-11-16 23:00 -- 0.5M 정시 습도(%)
7680 -- 2018-11-17 00:00 -- 0.5M 정시 습도(%)
7681 -- 2018-11-17 01:00 -- 0.5M 정시 습도(%)
7682 -- 2018-11-17 02:00 -- 0.5M 정시 습도(%)
7683 -- 2018-11-17 03:00 -- 0.5M 정시 습도(%)
7684 -- 2018-11-17 04:00 -- 0.5M 정시 습도(%)
7685 -- 2018-11-17 05:00 -- 0.5M 정시 습도(%)
7686 -- 2018-11-17 06:00 -- 0.5M 정시 습도(%)
7687 -- 2018-11-17 07:00 -- 0.5M 정시 습도(%)
7688 -- 2018-11-17 08:00 -- 0.5M 정시 습도(%)
7689 -- 2018-11-17 09:00 -- 0.5M 정시 습도(%)
7690 -- 2018-11-17 10:00 -- 0.5M 정시 습도(%)
7691 -- 2018-11-17 11:00 -- 0.5M 정시 습도(%)
7692 -- 2018-11-17 12:00 -- 0.5M 정시 습도(%)
7693 -- 2018-11-17 13:00 -- 0.5M 정시 습도(%)
7694 -- 2018-11-17 14:00 -- 0.5M 정

...

7566 -- 2018-11-12 06:00 -- 정시 누적 반사복사(MJ/m2)
7567 -- 2018-11-12 07:00 -- 정시 누적 반사복사(MJ/m2)
7568 -- 2018-11-12 08:00 -- 정시 누적 반사복사(MJ/m2)
7569 -- 2018-11-12 09:00 -- 정시 누적 반사복사(MJ/m2)
7570 -- 2018-11-12 10:00 -- 정시 누적 반사복사(MJ/m2)
7571 -- 2018-11-12 11:00 -- 정시 누적 반사복사(MJ/m2)
7572 -- 2018-11-12 12:00 -- 정시 누적 반사복사(MJ/m2)
7573 -- 2018-11-12 13:00 -- 정시 누적 반사복사(MJ/m2)
7574 -- 2018-11-12 14:00 -- 정시 누적 반사복사(MJ/m2)
7575 -- 2018-11-12 15:00 -- 정시 누적 반사복사(MJ/m2)
7576 -- 2018-11-12 16:00 -- 정시 누적 반사복사(MJ/m2)
7577 -- 2018-11-12 17:00 -- 정시 누적 반사복사(MJ/m2)
7578 -- 2018-11-12 18:00 -- 정시 누적 반사복사(MJ/m2)
7579 -- 2018-11-12 19:00 -- 정시 누적 반사복사(MJ/m2)
7580 -- 2018-11-12 20:00 -- 정시 누적 반사복사(MJ/m2)
7581 -- 2018-11-12 21:00 -- 정시 누적 반사복사(MJ/m2)
7582 -- 2018-11-12 22:00 -- 정시 누적 반사복사(MJ/m2)
7583 -- 2018-11-12 23:00 -- 정시 누적 반사복사(MJ/m2)
7584 -- 2018-11-13 00:00 -- 정시 누적 반사복사(MJ/m2)
7585 -- 2018-11-13 01:00 -- 정시 누적 반사복사(MJ/m2)
7586 -- 2018-11-13 02:00 -- 정시 누적 반사복사(MJ/m2)
7587 -- 2018-11-13 03:00 -- 정시 누적 

7798 -- 2018-11-21 22:00 -- 정시 누적 반사복사(MJ/m2)
7799 -- 2018-11-21 23:00 -- 정시 누적 반사복사(MJ/m2)
7800 -- 2018-11-22 00:00 -- 정시 누적 반사복사(MJ/m2)
7801 -- 2018-11-22 01:00 -- 정시 누적 반사복사(MJ/m2)
7802 -- 2018-11-22 02:00 -- 정시 누적 반사복사(MJ/m2)
7803 -- 2018-11-22 03:00 -- 정시 누적 반사복사(MJ/m2)
7804 -- 2018-11-22 04:00 -- 정시 누적 반사복사(MJ/m2)
7805 -- 2018-11-22 05:00 -- 정시 누적 반사복사(MJ/m2)
7806 -- 2018-11-22 06:00 -- 정시 누적 반사복사(MJ/m2)
7807 -- 2018-11-22 07:00 -- 정시 누적 반사복사(MJ/m2)
7808 -- 2018-11-22 08:00 -- 정시 누적 반사복사(MJ/m2)
7809 -- 2018-11-22 09:00 -- 정시 누적 반사복사(MJ/m2)
7810 -- 2018-11-22 10:00 -- 정시 누적 반사복사(MJ/m2)
7811 -- 2018-11-22 11:00 -- 정시 누적 반사복사(MJ/m2)
7812 -- 2018-11-22 12:00 -- 정시 누적 반사복사(MJ/m2)
7813 -- 2018-11-22 13:00 -- 정시 누적 반사복사(MJ/m2)
7814 -- 2018-11-22 14:00 -- 정시 누적 반사복사(MJ/m2)
7815 -- 2018-11-22 15:00 -- 정시 누적 반사복사(MJ/m2)
7816 -- 2018-11-22 16:00 -- 정시 누적 반사복사(MJ/m2)
7817 -- 2018-11-22 17:00 -- 정시 누적 반사복사(MJ/m2)
7818 -- 2018-11-22 18:00 -- 정시 누적 반사복사(MJ/m2)
7819 -- 2018-11-22 19:00 -- 정시 누적 

8046 -- 2018-12-02 06:00 -- 정시 누적 반사복사(MJ/m2)
8047 -- 2018-12-02 07:00 -- 정시 누적 반사복사(MJ/m2)
8048 -- 2018-12-02 08:00 -- 정시 누적 반사복사(MJ/m2)
8049 -- 2018-12-02 09:00 -- 정시 누적 반사복사(MJ/m2)
8050 -- 2018-12-02 10:00 -- 정시 누적 반사복사(MJ/m2)
8051 -- 2018-12-02 11:00 -- 정시 누적 반사복사(MJ/m2)
8052 -- 2018-12-02 12:00 -- 정시 누적 반사복사(MJ/m2)
8053 -- 2018-12-02 13:00 -- 정시 누적 반사복사(MJ/m2)
8054 -- 2018-12-02 14:00 -- 정시 누적 반사복사(MJ/m2)
8055 -- 2018-12-02 15:00 -- 정시 누적 반사복사(MJ/m2)
8056 -- 2018-12-02 16:00 -- 정시 누적 반사복사(MJ/m2)
8057 -- 2018-12-02 17:00 -- 정시 누적 반사복사(MJ/m2)
8058 -- 2018-12-02 18:00 -- 정시 누적 반사복사(MJ/m2)
8059 -- 2018-12-02 19:00 -- 정시 누적 반사복사(MJ/m2)
8060 -- 2018-12-02 20:00 -- 정시 누적 반사복사(MJ/m2)
8061 -- 2018-12-02 21:00 -- 정시 누적 반사복사(MJ/m2)
8062 -- 2018-12-02 22:00 -- 정시 누적 반사복사(MJ/m2)
8063 -- 2018-12-02 23:00 -- 정시 누적 반사복사(MJ/m2)
8064 -- 2018-12-03 00:00 -- 정시 누적 반사복사(MJ/m2)
8065 -- 2018-12-03 01:00 -- 정시 누적 반사복사(MJ/m2)
8066 -- 2018-12-03 02:00 -- 정시 누적 반사복사(MJ/m2)
8067 -- 2018-12-03 03:00 -- 정시 누적 

8234 -- 2018-12-10 02:00 -- 정시 누적 반사복사(MJ/m2)
8235 -- 2018-12-10 03:00 -- 정시 누적 반사복사(MJ/m2)
8236 -- 2018-12-10 04:00 -- 정시 누적 반사복사(MJ/m2)
8237 -- 2018-12-10 05:00 -- 정시 누적 반사복사(MJ/m2)
8238 -- 2018-12-10 06:00 -- 정시 누적 반사복사(MJ/m2)
8239 -- 2018-12-10 07:00 -- 정시 누적 반사복사(MJ/m2)
8240 -- 2018-12-10 08:00 -- 정시 누적 반사복사(MJ/m2)
8241 -- 2018-12-10 09:00 -- 정시 누적 반사복사(MJ/m2)
8242 -- 2018-12-10 10:00 -- 정시 누적 반사복사(MJ/m2)
8243 -- 2018-12-10 11:00 -- 정시 누적 반사복사(MJ/m2)
8244 -- 2018-12-10 12:00 -- 정시 누적 반사복사(MJ/m2)
8245 -- 2018-12-10 13:00 -- 정시 누적 반사복사(MJ/m2)
8246 -- 2018-12-10 14:00 -- 정시 누적 반사복사(MJ/m2)
8247 -- 2018-12-10 15:00 -- 정시 누적 반사복사(MJ/m2)
8248 -- 2018-12-10 16:00 -- 정시 누적 반사복사(MJ/m2)
8249 -- 2018-12-10 17:00 -- 정시 누적 반사복사(MJ/m2)
8250 -- 2018-12-10 18:00 -- 정시 누적 반사복사(MJ/m2)
8251 -- 2018-12-10 19:00 -- 정시 누적 반사복사(MJ/m2)
8252 -- 2018-12-10 20:00 -- 정시 누적 반사복사(MJ/m2)
8253 -- 2018-12-10 21:00 -- 정시 누적 반사복사(MJ/m2)
8254 -- 2018-12-10 22:00 -- 정시 누적 반사복사(MJ/m2)
8255 -- 2018-12-10 23:00 -- 정시 누적 

8481 -- 2018-12-20 09:00 -- 정시 누적 반사복사(MJ/m2)
8482 -- 2018-12-20 10:00 -- 정시 누적 반사복사(MJ/m2)
8483 -- 2018-12-20 11:00 -- 정시 누적 반사복사(MJ/m2)
8484 -- 2018-12-20 12:00 -- 정시 누적 반사복사(MJ/m2)
8485 -- 2018-12-20 13:00 -- 정시 누적 반사복사(MJ/m2)
8486 -- 2018-12-20 14:00 -- 정시 누적 반사복사(MJ/m2)
8487 -- 2018-12-20 15:00 -- 정시 누적 반사복사(MJ/m2)
8488 -- 2018-12-20 16:00 -- 정시 누적 반사복사(MJ/m2)
8489 -- 2018-12-20 17:00 -- 정시 누적 반사복사(MJ/m2)
8490 -- 2018-12-20 18:00 -- 정시 누적 반사복사(MJ/m2)
8491 -- 2018-12-20 19:00 -- 정시 누적 반사복사(MJ/m2)
8492 -- 2018-12-20 20:00 -- 정시 누적 반사복사(MJ/m2)
8493 -- 2018-12-20 21:00 -- 정시 누적 반사복사(MJ/m2)
8494 -- 2018-12-20 22:00 -- 정시 누적 반사복사(MJ/m2)
8495 -- 2018-12-20 23:00 -- 정시 누적 반사복사(MJ/m2)
8496 -- 2018-12-21 00:00 -- 정시 누적 반사복사(MJ/m2)
8497 -- 2018-12-21 01:00 -- 정시 누적 반사복사(MJ/m2)
8498 -- 2018-12-21 02:00 -- 정시 누적 반사복사(MJ/m2)
8499 -- 2018-12-21 03:00 -- 정시 누적 반사복사(MJ/m2)
8500 -- 2018-12-21 04:00 -- 정시 누적 반사복사(MJ/m2)
8501 -- 2018-12-21 05:00 -- 정시 누적 반사복사(MJ/m2)
8502 -- 2018-12-21 06:00 -- 정시 누적 

In [441]:
# 5칸만 결측치가 있을 시 앞 뒤 데이터의 평균값으로 결측치 대체
col = data_col[0]
for i in tqdm_notebook(data_col):
    for q in range(len(sup)):
        try:
            if sup[i].isnull()[q] == True and sup[i].isnull()[q+1] == True and sup[i].isnull()[q+2] == True and sup[i].isnull()[q+3] == True and sup[i].isnull()[q+4] == True:
                print(q, '--', sup['일시'][q] , '--',i)
                sup[i][q] = (sup[i][q-1] + sup[i][q+5]) / 2
                sup[i][q+1] = sup[i][q]
                sup[i][q+2] = sup[i][q]
                sup[i][q+3] = sup[i][q]
                sup[i][q+4] = sup[i][q]
        except:
            pass

C:\Users\leedo\AppData\Local\Temp\ipykernel_3120\3630409750.py:3: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  for i in tqdm_notebook(data_col):


  0%|          | 0/20 [00:00<?, ?it/s]

7235 -- 2018-10-29 11:00 -- 0.5M 정시 습도(%)
7236 -- 2018-10-29 12:00 -- 0.5M 정시 습도(%)
7237 -- 2018-10-29 13:00 -- 0.5M 정시 습도(%)
7238 -- 2018-10-29 14:00 -- 0.5M 정시 습도(%)
7239 -- 2018-10-29 15:00 -- 0.5M 정시 습도(%)
7240 -- 2018-10-29 16:00 -- 0.5M 정시 습도(%)
7241 -- 2018-10-29 17:00 -- 0.5M 정시 습도(%)
7242 -- 2018-10-29 18:00 -- 0.5M 정시 습도(%)
7243 -- 2018-10-29 19:00 -- 0.5M 정시 습도(%)
7244 -- 2018-10-29 20:00 -- 0.5M 정시 습도(%)
7245 -- 2018-10-29 21:00 -- 0.5M 정시 습도(%)
7246 -- 2018-10-29 22:00 -- 0.5M 정시 습도(%)
7247 -- 2018-10-29 23:00 -- 0.5M 정시 습도(%)
7248 -- 2018-10-30 00:00 -- 0.5M 정시 습도(%)
7249 -- 2018-10-30 01:00 -- 0.5M 정시 습도(%)
7250 -- 2018-10-30 02:00 -- 0.5M 정시 습도(%)
7251 -- 2018-10-30 03:00 -- 0.5M 정시 습도(%)
7252 -- 2018-10-30 04:00 -- 0.5M 정시 습도(%)
7253 -- 2018-10-30 05:00 -- 0.5M 정시 습도(%)
7254 -- 2018-10-30 06:00 -- 0.5M 정시 습도(%)
7255 -- 2018-10-30 07:00 -- 0.5M 정시 습도(%)
7256 -- 2018-10-30 08:00 -- 0.5M 정시 습도(%)
7257 -- 2018-10-30 09:00 -- 0.5M 정시 습도(%)
7258 -- 2018-10-30 10:00 -- 0.5M 정

7432 -- 2018-11-06 16:00 -- 0.5M 정시 습도(%)
7433 -- 2018-11-06 17:00 -- 0.5M 정시 습도(%)
7434 -- 2018-11-06 18:00 -- 0.5M 정시 습도(%)
7435 -- 2018-11-06 19:00 -- 0.5M 정시 습도(%)
7436 -- 2018-11-06 20:00 -- 0.5M 정시 습도(%)
7437 -- 2018-11-06 21:00 -- 0.5M 정시 습도(%)
7438 -- 2018-11-06 22:00 -- 0.5M 정시 습도(%)
7439 -- 2018-11-06 23:00 -- 0.5M 정시 습도(%)
7440 -- 2018-11-07 00:00 -- 0.5M 정시 습도(%)
7441 -- 2018-11-07 01:00 -- 0.5M 정시 습도(%)
7442 -- 2018-11-07 02:00 -- 0.5M 정시 습도(%)
7443 -- 2018-11-07 03:00 -- 0.5M 정시 습도(%)
7444 -- 2018-11-07 04:00 -- 0.5M 정시 습도(%)
7445 -- 2018-11-07 05:00 -- 0.5M 정시 습도(%)
7446 -- 2018-11-07 06:00 -- 0.5M 정시 습도(%)
7447 -- 2018-11-07 07:00 -- 0.5M 정시 습도(%)
7448 -- 2018-11-07 08:00 -- 0.5M 정시 습도(%)
7449 -- 2018-11-07 09:00 -- 0.5M 정시 습도(%)
7450 -- 2018-11-07 10:00 -- 0.5M 정시 습도(%)
7451 -- 2018-11-07 11:00 -- 0.5M 정시 습도(%)
7452 -- 2018-11-07 12:00 -- 0.5M 정시 습도(%)
7453 -- 2018-11-07 13:00 -- 0.5M 정시 습도(%)
7454 -- 2018-11-07 14:00 -- 0.5M 정시 습도(%)
7455 -- 2018-11-07 15:00 -- 0.5M 정

7693 -- 2018-11-17 13:00 -- 0.5M 정시 습도(%)
7694 -- 2018-11-17 14:00 -- 0.5M 정시 습도(%)
7695 -- 2018-11-17 15:00 -- 0.5M 정시 습도(%)
7696 -- 2018-11-17 16:00 -- 0.5M 정시 습도(%)
7697 -- 2018-11-17 17:00 -- 0.5M 정시 습도(%)
7698 -- 2018-11-17 18:00 -- 0.5M 정시 습도(%)
7699 -- 2018-11-17 19:00 -- 0.5M 정시 습도(%)
7700 -- 2018-11-17 20:00 -- 0.5M 정시 습도(%)
7701 -- 2018-11-17 21:00 -- 0.5M 정시 습도(%)
7702 -- 2018-11-17 22:00 -- 0.5M 정시 습도(%)
7703 -- 2018-11-17 23:00 -- 0.5M 정시 습도(%)
7704 -- 2018-11-18 00:00 -- 0.5M 정시 습도(%)
7705 -- 2018-11-18 01:00 -- 0.5M 정시 습도(%)
7706 -- 2018-11-18 02:00 -- 0.5M 정시 습도(%)
7707 -- 2018-11-18 03:00 -- 0.5M 정시 습도(%)
7708 -- 2018-11-18 04:00 -- 0.5M 정시 습도(%)
7709 -- 2018-11-18 05:00 -- 0.5M 정시 습도(%)
7710 -- 2018-11-18 06:00 -- 0.5M 정시 습도(%)
7711 -- 2018-11-18 07:00 -- 0.5M 정시 습도(%)
7712 -- 2018-11-18 08:00 -- 0.5M 정시 습도(%)
7713 -- 2018-11-18 09:00 -- 0.5M 정시 습도(%)
7714 -- 2018-11-18 10:00 -- 0.5M 정시 습도(%)
7715 -- 2018-11-18 11:00 -- 0.5M 정시 습도(%)
7716 -- 2018-11-18 12:00 -- 0.5M 정

...

7832 -- 2018-11-23 08:00 -- 정시 누적 반사복사(MJ/m2)
7833 -- 2018-11-23 09:00 -- 정시 누적 반사복사(MJ/m2)
7834 -- 2018-11-23 10:00 -- 정시 누적 반사복사(MJ/m2)
7835 -- 2018-11-23 11:00 -- 정시 누적 반사복사(MJ/m2)
7836 -- 2018-11-23 12:00 -- 정시 누적 반사복사(MJ/m2)
7837 -- 2018-11-23 13:00 -- 정시 누적 반사복사(MJ/m2)
7838 -- 2018-11-23 14:00 -- 정시 누적 반사복사(MJ/m2)
7839 -- 2018-11-23 15:00 -- 정시 누적 반사복사(MJ/m2)
7840 -- 2018-11-23 16:00 -- 정시 누적 반사복사(MJ/m2)
7841 -- 2018-11-23 17:00 -- 정시 누적 반사복사(MJ/m2)
7842 -- 2018-11-23 18:00 -- 정시 누적 반사복사(MJ/m2)
7843 -- 2018-11-23 19:00 -- 정시 누적 반사복사(MJ/m2)
7844 -- 2018-11-23 20:00 -- 정시 누적 반사복사(MJ/m2)
7845 -- 2018-11-23 21:00 -- 정시 누적 반사복사(MJ/m2)
7846 -- 2018-11-23 22:00 -- 정시 누적 반사복사(MJ/m2)
7847 -- 2018-11-23 23:00 -- 정시 누적 반사복사(MJ/m2)
7848 -- 2018-11-24 00:00 -- 정시 누적 반사복사(MJ/m2)
7849 -- 2018-11-24 01:00 -- 정시 누적 반사복사(MJ/m2)
7850 -- 2018-11-24 02:00 -- 정시 누적 반사복사(MJ/m2)
7851 -- 2018-11-24 03:00 -- 정시 누적 반사복사(MJ/m2)
7852 -- 2018-11-24 04:00 -- 정시 누적 반사복사(MJ/m2)
7853 -- 2018-11-24 05:00 -- 정시 누적 

8084 -- 2018-12-03 20:00 -- 정시 누적 반사복사(MJ/m2)
8085 -- 2018-12-03 21:00 -- 정시 누적 반사복사(MJ/m2)
8086 -- 2018-12-03 22:00 -- 정시 누적 반사복사(MJ/m2)
8087 -- 2018-12-03 23:00 -- 정시 누적 반사복사(MJ/m2)
8088 -- 2018-12-04 00:00 -- 정시 누적 반사복사(MJ/m2)
8089 -- 2018-12-04 01:00 -- 정시 누적 반사복사(MJ/m2)
8090 -- 2018-12-04 02:00 -- 정시 누적 반사복사(MJ/m2)
8091 -- 2018-12-04 03:00 -- 정시 누적 반사복사(MJ/m2)
8092 -- 2018-12-04 04:00 -- 정시 누적 반사복사(MJ/m2)
8093 -- 2018-12-04 05:00 -- 정시 누적 반사복사(MJ/m2)
8094 -- 2018-12-04 06:00 -- 정시 누적 반사복사(MJ/m2)
8095 -- 2018-12-04 07:00 -- 정시 누적 반사복사(MJ/m2)
8096 -- 2018-12-04 08:00 -- 정시 누적 반사복사(MJ/m2)
8097 -- 2018-12-04 09:00 -- 정시 누적 반사복사(MJ/m2)
8098 -- 2018-12-04 10:00 -- 정시 누적 반사복사(MJ/m2)
8099 -- 2018-12-04 11:00 -- 정시 누적 반사복사(MJ/m2)
8100 -- 2018-12-04 12:00 -- 정시 누적 반사복사(MJ/m2)
8101 -- 2018-12-04 13:00 -- 정시 누적 반사복사(MJ/m2)
8102 -- 2018-12-04 14:00 -- 정시 누적 반사복사(MJ/m2)
8103 -- 2018-12-04 15:00 -- 정시 누적 반사복사(MJ/m2)
8104 -- 2018-12-04 16:00 -- 정시 누적 반사복사(MJ/m2)
8105 -- 2018-12-04 17:00 -- 정시 누적 

8287 -- 2018-12-12 07:00 -- 정시 누적 반사복사(MJ/m2)
8288 -- 2018-12-12 08:00 -- 정시 누적 반사복사(MJ/m2)
8289 -- 2018-12-12 09:00 -- 정시 누적 반사복사(MJ/m2)
8290 -- 2018-12-12 10:00 -- 정시 누적 반사복사(MJ/m2)
8291 -- 2018-12-12 11:00 -- 정시 누적 반사복사(MJ/m2)
8292 -- 2018-12-12 12:00 -- 정시 누적 반사복사(MJ/m2)
8293 -- 2018-12-12 13:00 -- 정시 누적 반사복사(MJ/m2)
8294 -- 2018-12-12 14:00 -- 정시 누적 반사복사(MJ/m2)
8295 -- 2018-12-12 15:00 -- 정시 누적 반사복사(MJ/m2)
8296 -- 2018-12-12 16:00 -- 정시 누적 반사복사(MJ/m2)
8297 -- 2018-12-12 17:00 -- 정시 누적 반사복사(MJ/m2)
8298 -- 2018-12-12 18:00 -- 정시 누적 반사복사(MJ/m2)
8299 -- 2018-12-12 19:00 -- 정시 누적 반사복사(MJ/m2)
8300 -- 2018-12-12 20:00 -- 정시 누적 반사복사(MJ/m2)
8301 -- 2018-12-12 21:00 -- 정시 누적 반사복사(MJ/m2)
8302 -- 2018-12-12 22:00 -- 정시 누적 반사복사(MJ/m2)
8303 -- 2018-12-12 23:00 -- 정시 누적 반사복사(MJ/m2)
8304 -- 2018-12-13 00:00 -- 정시 누적 반사복사(MJ/m2)
8305 -- 2018-12-13 01:00 -- 정시 누적 반사복사(MJ/m2)
8306 -- 2018-12-13 02:00 -- 정시 누적 반사복사(MJ/m2)
8307 -- 2018-12-13 03:00 -- 정시 누적 반사복사(MJ/m2)
8308 -- 2018-12-13 04:00 -- 정시 누적 

8489 -- 2018-12-20 17:00 -- 정시 누적 반사복사(MJ/m2)
8490 -- 2018-12-20 18:00 -- 정시 누적 반사복사(MJ/m2)
8491 -- 2018-12-20 19:00 -- 정시 누적 반사복사(MJ/m2)
8492 -- 2018-12-20 20:00 -- 정시 누적 반사복사(MJ/m2)
8493 -- 2018-12-20 21:00 -- 정시 누적 반사복사(MJ/m2)
8494 -- 2018-12-20 22:00 -- 정시 누적 반사복사(MJ/m2)
8495 -- 2018-12-20 23:00 -- 정시 누적 반사복사(MJ/m2)
8496 -- 2018-12-21 00:00 -- 정시 누적 반사복사(MJ/m2)
8497 -- 2018-12-21 01:00 -- 정시 누적 반사복사(MJ/m2)
8498 -- 2018-12-21 02:00 -- 정시 누적 반사복사(MJ/m2)
8499 -- 2018-12-21 03:00 -- 정시 누적 반사복사(MJ/m2)
8500 -- 2018-12-21 04:00 -- 정시 누적 반사복사(MJ/m2)
8501 -- 2018-12-21 05:00 -- 정시 누적 반사복사(MJ/m2)
8502 -- 2018-12-21 06:00 -- 정시 누적 반사복사(MJ/m2)
8503 -- 2018-12-21 07:00 -- 정시 누적 반사복사(MJ/m2)
8504 -- 2018-12-21 08:00 -- 정시 누적 반사복사(MJ/m2)
8505 -- 2018-12-21 09:00 -- 정시 누적 반사복사(MJ/m2)
8506 -- 2018-12-21 10:00 -- 정시 누적 반사복사(MJ/m2)
8507 -- 2018-12-21 11:00 -- 정시 누적 반사복사(MJ/m2)
8508 -- 2018-12-21 12:00 -- 정시 누적 반사복사(MJ/m2)
8509 -- 2018-12-21 13:00 -- 정시 누적 반사복사(MJ/m2)
8510 -- 2018-12-21 14:00 -- 정시 누적 

8687 -- 2018-12-28 23:00 -- 정시 누적 반사복사(MJ/m2)
8688 -- 2018-12-29 00:00 -- 정시 누적 반사복사(MJ/m2)
8689 -- 2018-12-29 01:00 -- 정시 누적 반사복사(MJ/m2)
8690 -- 2018-12-29 02:00 -- 정시 누적 반사복사(MJ/m2)
8691 -- 2018-12-29 03:00 -- 정시 누적 반사복사(MJ/m2)
8692 -- 2018-12-29 04:00 -- 정시 누적 반사복사(MJ/m2)
8693 -- 2018-12-29 05:00 -- 정시 누적 반사복사(MJ/m2)
8694 -- 2018-12-29 06:00 -- 정시 누적 반사복사(MJ/m2)
8695 -- 2018-12-29 07:00 -- 정시 누적 반사복사(MJ/m2)
8696 -- 2018-12-29 08:00 -- 정시 누적 반사복사(MJ/m2)
8697 -- 2018-12-29 09:00 -- 정시 누적 반사복사(MJ/m2)
8698 -- 2018-12-29 10:00 -- 정시 누적 반사복사(MJ/m2)
8699 -- 2018-12-29 11:00 -- 정시 누적 반사복사(MJ/m2)
8700 -- 2018-12-29 12:00 -- 정시 누적 반사복사(MJ/m2)
8701 -- 2018-12-29 13:00 -- 정시 누적 반사복사(MJ/m2)
8702 -- 2018-12-29 14:00 -- 정시 누적 반사복사(MJ/m2)
8703 -- 2018-12-29 15:00 -- 정시 누적 반사복사(MJ/m2)
8704 -- 2018-12-29 16:00 -- 정시 누적 반사복사(MJ/m2)
8705 -- 2018-12-29 17:00 -- 정시 누적 반사복사(MJ/m2)
8706 -- 2018-12-29 18:00 -- 정시 누적 반사복사(MJ/m2)
8707 -- 2018-12-29 19:00 -- 정시 누적 반사복사(MJ/m2)
8708 -- 2018-12-29 20:00 -- 정시 누적 

In [442]:
# 6칸만 결측치가 있을 시 앞 뒤 데이터의 평균값으로 결측치 대체
col = data_col[0]
for i in tqdm_notebook(data_col):
    for q in range(len(sup)):
        try:
            if sup[i].isnull()[q] == True and sup[i].isnull()[q+1] == True and sup[i].isnull()[q+2] == True and sup[i].isnull()[q+3] == True and sup[i].isnull()[q+5] == True and sup[i].isnull()[q+5] == True:
                print(q, '--', sup['일시'][q] , '--',i)
                sup[i][q] = (sup[i][q-1] + sup[i][q+6]) / 2
                sup[i][q+1] = sup[i][q]
                sup[i][q+2] = sup[i][q]
                sup[i][q+3] = sup[i][q]
                sup[i][q+4] = sup[i][q]
                sup[i][q+5] = sup[i][q]
        except:
            pass

C:\Users\leedo\AppData\Local\Temp\ipykernel_3120\1084076583.py:3: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  for i in tqdm_notebook(data_col):


  0%|          | 0/20 [00:00<?, ?it/s]

7235 -- 2018-10-29 11:00 -- 0.5M 정시 습도(%)
7236 -- 2018-10-29 12:00 -- 0.5M 정시 습도(%)
7237 -- 2018-10-29 13:00 -- 0.5M 정시 습도(%)
7238 -- 2018-10-29 14:00 -- 0.5M 정시 습도(%)
7239 -- 2018-10-29 15:00 -- 0.5M 정시 습도(%)
7240 -- 2018-10-29 16:00 -- 0.5M 정시 습도(%)
7241 -- 2018-10-29 17:00 -- 0.5M 정시 습도(%)
7242 -- 2018-10-29 18:00 -- 0.5M 정시 습도(%)
7243 -- 2018-10-29 19:00 -- 0.5M 정시 습도(%)
7244 -- 2018-10-29 20:00 -- 0.5M 정시 습도(%)
7245 -- 2018-10-29 21:00 -- 0.5M 정시 습도(%)
7246 -- 2018-10-29 22:00 -- 0.5M 정시 습도(%)
7247 -- 2018-10-29 23:00 -- 0.5M 정시 습도(%)
7248 -- 2018-10-30 00:00 -- 0.5M 정시 습도(%)
7249 -- 2018-10-30 01:00 -- 0.5M 정시 습도(%)
7250 -- 2018-10-30 02:00 -- 0.5M 정시 습도(%)
7251 -- 2018-10-30 03:00 -- 0.5M 정시 습도(%)
7252 -- 2018-10-30 04:00 -- 0.5M 정시 습도(%)
7253 -- 2018-10-30 05:00 -- 0.5M 정시 습도(%)
7254 -- 2018-10-30 06:00 -- 0.5M 정시 습도(%)
7255 -- 2018-10-30 07:00 -- 0.5M 정시 습도(%)
7256 -- 2018-10-30 08:00 -- 0.5M 정시 습도(%)
7257 -- 2018-10-30 09:00 -- 0.5M 정시 습도(%)
7258 -- 2018-10-30 10:00 -- 0.5M 정

7468 -- 2018-11-08 04:00 -- 0.5M 정시 습도(%)
7469 -- 2018-11-08 05:00 -- 0.5M 정시 습도(%)
7470 -- 2018-11-08 06:00 -- 0.5M 정시 습도(%)
7471 -- 2018-11-08 07:00 -- 0.5M 정시 습도(%)
7472 -- 2018-11-08 08:00 -- 0.5M 정시 습도(%)
7473 -- 2018-11-08 09:00 -- 0.5M 정시 습도(%)
7474 -- 2018-11-08 10:00 -- 0.5M 정시 습도(%)
7475 -- 2018-11-08 11:00 -- 0.5M 정시 습도(%)
7476 -- 2018-11-08 12:00 -- 0.5M 정시 습도(%)
7477 -- 2018-11-08 13:00 -- 0.5M 정시 습도(%)
7478 -- 2018-11-08 14:00 -- 0.5M 정시 습도(%)
7479 -- 2018-11-08 15:00 -- 0.5M 정시 습도(%)
7480 -- 2018-11-08 16:00 -- 0.5M 정시 습도(%)
7481 -- 2018-11-08 17:00 -- 0.5M 정시 습도(%)
7482 -- 2018-11-08 18:00 -- 0.5M 정시 습도(%)
7483 -- 2018-11-08 19:00 -- 0.5M 정시 습도(%)
7484 -- 2018-11-08 20:00 -- 0.5M 정시 습도(%)
7485 -- 2018-11-08 21:00 -- 0.5M 정시 습도(%)
7486 -- 2018-11-08 22:00 -- 0.5M 정시 습도(%)
7487 -- 2018-11-08 23:00 -- 0.5M 정시 습도(%)
7488 -- 2018-11-09 00:00 -- 0.5M 정시 습도(%)
7489 -- 2018-11-09 01:00 -- 0.5M 정시 습도(%)
7490 -- 2018-11-09 02:00 -- 0.5M 정시 습도(%)
7491 -- 2018-11-09 03:00 -- 0.5M 정

7712 -- 2018-11-18 08:00 -- 0.5M 정시 습도(%)
7713 -- 2018-11-18 09:00 -- 0.5M 정시 습도(%)
7714 -- 2018-11-18 10:00 -- 0.5M 정시 습도(%)
7715 -- 2018-11-18 11:00 -- 0.5M 정시 습도(%)
7716 -- 2018-11-18 12:00 -- 0.5M 정시 습도(%)
7717 -- 2018-11-18 13:00 -- 0.5M 정시 습도(%)
7718 -- 2018-11-18 14:00 -- 0.5M 정시 습도(%)
7719 -- 2018-11-18 15:00 -- 0.5M 정시 습도(%)
7720 -- 2018-11-18 16:00 -- 0.5M 정시 습도(%)
7721 -- 2018-11-18 17:00 -- 0.5M 정시 습도(%)
7722 -- 2018-11-18 18:00 -- 0.5M 정시 습도(%)
7723 -- 2018-11-18 19:00 -- 0.5M 정시 습도(%)
7724 -- 2018-11-18 20:00 -- 0.5M 정시 습도(%)
7725 -- 2018-11-18 21:00 -- 0.5M 정시 습도(%)
7726 -- 2018-11-18 22:00 -- 0.5M 정시 습도(%)
7727 -- 2018-11-18 23:00 -- 0.5M 정시 습도(%)
7728 -- 2018-11-19 00:00 -- 0.5M 정시 습도(%)
7729 -- 2018-11-19 01:00 -- 0.5M 정시 습도(%)
7730 -- 2018-11-19 02:00 -- 0.5M 정시 습도(%)
7731 -- 2018-11-19 03:00 -- 0.5M 정시 습도(%)
7732 -- 2018-11-19 04:00 -- 0.5M 정시 습도(%)
7733 -- 2018-11-19 05:00 -- 0.5M 정시 습도(%)
7734 -- 2018-11-19 06:00 -- 0.5M 정시 습도(%)
7735 -- 2018-11-19 07:00 -- 0.5M 정

...

7639 -- 2018-11-15 07:00 -- 정시 누적 반사복사(MJ/m2)
7640 -- 2018-11-15 08:00 -- 정시 누적 반사복사(MJ/m2)
7641 -- 2018-11-15 09:00 -- 정시 누적 반사복사(MJ/m2)
7642 -- 2018-11-15 10:00 -- 정시 누적 반사복사(MJ/m2)
7643 -- 2018-11-15 11:00 -- 정시 누적 반사복사(MJ/m2)
7644 -- 2018-11-15 12:00 -- 정시 누적 반사복사(MJ/m2)
7645 -- 2018-11-15 13:00 -- 정시 누적 반사복사(MJ/m2)
7646 -- 2018-11-15 14:00 -- 정시 누적 반사복사(MJ/m2)
7647 -- 2018-11-15 15:00 -- 정시 누적 반사복사(MJ/m2)
7648 -- 2018-11-15 16:00 -- 정시 누적 반사복사(MJ/m2)
7649 -- 2018-11-15 17:00 -- 정시 누적 반사복사(MJ/m2)
7650 -- 2018-11-15 18:00 -- 정시 누적 반사복사(MJ/m2)
7651 -- 2018-11-15 19:00 -- 정시 누적 반사복사(MJ/m2)
7652 -- 2018-11-15 20:00 -- 정시 누적 반사복사(MJ/m2)
7653 -- 2018-11-15 21:00 -- 정시 누적 반사복사(MJ/m2)
7654 -- 2018-11-15 22:00 -- 정시 누적 반사복사(MJ/m2)
7655 -- 2018-11-15 23:00 -- 정시 누적 반사복사(MJ/m2)
7656 -- 2018-11-16 00:00 -- 정시 누적 반사복사(MJ/m2)
7657 -- 2018-11-16 01:00 -- 정시 누적 반사복사(MJ/m2)
7658 -- 2018-11-16 02:00 -- 정시 누적 반사복사(MJ/m2)
7659 -- 2018-11-16 03:00 -- 정시 누적 반사복사(MJ/m2)
7660 -- 2018-11-16 04:00 -- 정시 누적 

7904 -- 2018-11-26 08:00 -- 정시 누적 반사복사(MJ/m2)
7905 -- 2018-11-26 09:00 -- 정시 누적 반사복사(MJ/m2)
7906 -- 2018-11-26 10:00 -- 정시 누적 반사복사(MJ/m2)
7907 -- 2018-11-26 11:00 -- 정시 누적 반사복사(MJ/m2)
7908 -- 2018-11-26 12:00 -- 정시 누적 반사복사(MJ/m2)
7909 -- 2018-11-26 13:00 -- 정시 누적 반사복사(MJ/m2)
7910 -- 2018-11-26 14:00 -- 정시 누적 반사복사(MJ/m2)
7911 -- 2018-11-26 15:00 -- 정시 누적 반사복사(MJ/m2)
7912 -- 2018-11-26 16:00 -- 정시 누적 반사복사(MJ/m2)
7913 -- 2018-11-26 17:00 -- 정시 누적 반사복사(MJ/m2)
7914 -- 2018-11-26 18:00 -- 정시 누적 반사복사(MJ/m2)
7915 -- 2018-11-26 19:00 -- 정시 누적 반사복사(MJ/m2)
7916 -- 2018-11-26 20:00 -- 정시 누적 반사복사(MJ/m2)
7917 -- 2018-11-26 21:00 -- 정시 누적 반사복사(MJ/m2)
7918 -- 2018-11-26 22:00 -- 정시 누적 반사복사(MJ/m2)
7919 -- 2018-11-26 23:00 -- 정시 누적 반사복사(MJ/m2)
7920 -- 2018-11-27 00:00 -- 정시 누적 반사복사(MJ/m2)
7921 -- 2018-11-27 01:00 -- 정시 누적 반사복사(MJ/m2)
7922 -- 2018-11-27 02:00 -- 정시 누적 반사복사(MJ/m2)
7923 -- 2018-11-27 03:00 -- 정시 누적 반사복사(MJ/m2)
7924 -- 2018-11-27 04:00 -- 정시 누적 반사복사(MJ/m2)
7925 -- 2018-11-27 05:00 -- 정시 누적 

8113 -- 2018-12-05 01:00 -- 정시 누적 반사복사(MJ/m2)
8114 -- 2018-12-05 02:00 -- 정시 누적 반사복사(MJ/m2)
8115 -- 2018-12-05 03:00 -- 정시 누적 반사복사(MJ/m2)
8116 -- 2018-12-05 04:00 -- 정시 누적 반사복사(MJ/m2)
8117 -- 2018-12-05 05:00 -- 정시 누적 반사복사(MJ/m2)
8118 -- 2018-12-05 06:00 -- 정시 누적 반사복사(MJ/m2)
8119 -- 2018-12-05 07:00 -- 정시 누적 반사복사(MJ/m2)
8120 -- 2018-12-05 08:00 -- 정시 누적 반사복사(MJ/m2)
8121 -- 2018-12-05 09:00 -- 정시 누적 반사복사(MJ/m2)
8122 -- 2018-12-05 10:00 -- 정시 누적 반사복사(MJ/m2)
8123 -- 2018-12-05 11:00 -- 정시 누적 반사복사(MJ/m2)
8124 -- 2018-12-05 12:00 -- 정시 누적 반사복사(MJ/m2)
8125 -- 2018-12-05 13:00 -- 정시 누적 반사복사(MJ/m2)
8126 -- 2018-12-05 14:00 -- 정시 누적 반사복사(MJ/m2)
8127 -- 2018-12-05 15:00 -- 정시 누적 반사복사(MJ/m2)
8128 -- 2018-12-05 16:00 -- 정시 누적 반사복사(MJ/m2)
8129 -- 2018-12-05 17:00 -- 정시 누적 반사복사(MJ/m2)
8130 -- 2018-12-05 18:00 -- 정시 누적 반사복사(MJ/m2)
8131 -- 2018-12-05 19:00 -- 정시 누적 반사복사(MJ/m2)
8132 -- 2018-12-05 20:00 -- 정시 누적 반사복사(MJ/m2)
8133 -- 2018-12-05 21:00 -- 정시 누적 반사복사(MJ/m2)
8134 -- 2018-12-05 22:00 -- 정시 누적 

8371 -- 2018-12-15 19:00 -- 정시 누적 반사복사(MJ/m2)
8372 -- 2018-12-15 20:00 -- 정시 누적 반사복사(MJ/m2)
8373 -- 2018-12-15 21:00 -- 정시 누적 반사복사(MJ/m2)
8374 -- 2018-12-15 22:00 -- 정시 누적 반사복사(MJ/m2)
8375 -- 2018-12-15 23:00 -- 정시 누적 반사복사(MJ/m2)
8376 -- 2018-12-16 00:00 -- 정시 누적 반사복사(MJ/m2)
8377 -- 2018-12-16 01:00 -- 정시 누적 반사복사(MJ/m2)
8378 -- 2018-12-16 02:00 -- 정시 누적 반사복사(MJ/m2)
8379 -- 2018-12-16 03:00 -- 정시 누적 반사복사(MJ/m2)
8380 -- 2018-12-16 04:00 -- 정시 누적 반사복사(MJ/m2)
8381 -- 2018-12-16 05:00 -- 정시 누적 반사복사(MJ/m2)
8382 -- 2018-12-16 06:00 -- 정시 누적 반사복사(MJ/m2)
8383 -- 2018-12-16 07:00 -- 정시 누적 반사복사(MJ/m2)
8384 -- 2018-12-16 08:00 -- 정시 누적 반사복사(MJ/m2)
8385 -- 2018-12-16 09:00 -- 정시 누적 반사복사(MJ/m2)
8386 -- 2018-12-16 10:00 -- 정시 누적 반사복사(MJ/m2)
8387 -- 2018-12-16 11:00 -- 정시 누적 반사복사(MJ/m2)
8388 -- 2018-12-16 12:00 -- 정시 누적 반사복사(MJ/m2)
8389 -- 2018-12-16 13:00 -- 정시 누적 반사복사(MJ/m2)
8390 -- 2018-12-16 14:00 -- 정시 누적 반사복사(MJ/m2)
8391 -- 2018-12-16 15:00 -- 정시 누적 반사복사(MJ/m2)
8392 -- 2018-12-16 16:00 -- 정시 누적 

8623 -- 2018-12-26 07:00 -- 정시 누적 반사복사(MJ/m2)
8624 -- 2018-12-26 08:00 -- 정시 누적 반사복사(MJ/m2)
8625 -- 2018-12-26 09:00 -- 정시 누적 반사복사(MJ/m2)
8626 -- 2018-12-26 10:00 -- 정시 누적 반사복사(MJ/m2)
8627 -- 2018-12-26 11:00 -- 정시 누적 반사복사(MJ/m2)
8628 -- 2018-12-26 12:00 -- 정시 누적 반사복사(MJ/m2)
8629 -- 2018-12-26 13:00 -- 정시 누적 반사복사(MJ/m2)
8630 -- 2018-12-26 14:00 -- 정시 누적 반사복사(MJ/m2)
8631 -- 2018-12-26 15:00 -- 정시 누적 반사복사(MJ/m2)
8632 -- 2018-12-26 16:00 -- 정시 누적 반사복사(MJ/m2)
8633 -- 2018-12-26 17:00 -- 정시 누적 반사복사(MJ/m2)
8634 -- 2018-12-26 18:00 -- 정시 누적 반사복사(MJ/m2)
8635 -- 2018-12-26 19:00 -- 정시 누적 반사복사(MJ/m2)
8636 -- 2018-12-26 20:00 -- 정시 누적 반사복사(MJ/m2)
8637 -- 2018-12-26 21:00 -- 정시 누적 반사복사(MJ/m2)
8638 -- 2018-12-26 22:00 -- 정시 누적 반사복사(MJ/m2)
8639 -- 2018-12-26 23:00 -- 정시 누적 반사복사(MJ/m2)
8640 -- 2018-12-27 00:00 -- 정시 누적 반사복사(MJ/m2)
8641 -- 2018-12-27 01:00 -- 정시 누적 반사복사(MJ/m2)
8642 -- 2018-12-27 02:00 -- 정시 누적 반사복사(MJ/m2)
8643 -- 2018-12-27 03:00 -- 정시 누적 반사복사(MJ/m2)
8644 -- 2018-12-27 04:00 -- 정시 누적 

In [443]:
# 컬럼 개별적으로 5시간 이상 결측치가 있는 경우 연속한 날짜 범위를 추출
# 결측치 날짜 + 시간, 결측이 있는 해당 칼럼을 입력
for q in range(len(data_col)):

    lost_data=[]
    col = data_col[q]
    print(q)
    for i in range(len(sup)):
        if sup[col].isnull()[i] == True and sup[col].isnull()[i+1] == True and sup[col].isnull()[i+2] == True and sup[col].isnull()[i+3] == True and sup[col].isnull()[i+4] == True:
            print(sup['일시'][i], col)
            lost_data.append(sup['일시'][i])
            lost_data.append(sup['일시'][i+1])
            lost_data.append(sup['일시'][i+2])
            lost_data.append(sup['일시'][i+3])
            lost_data.append(sup['일시'][i+4])

    lost_data = sorted(list(set(lost_data)))        
    if len(lost_data) != 0:

        lost_index = []
        for w in range(len(lost_data) - 1):
            if len(pd.date_range(lost_data[w], lost_data[w+1], freq='H')) != 2:
                print(lost_data[w], i, lost_data[w+1], w+1)
                lost_index.append(w)
                lost_index.append(w+1)
        lost_index.insert(0, 0)
        lost_index.append(len(lost_data)-1)

        # 장기 결측 데이터 시작과 끝
        for e in tqdm_notebook(range(0, len(lost_index) -1, 2)):
            first = lost_data[lost_index[e]]
            end = lost_data[lost_index[e+1]]

            # 데이터프레임 날짜에서 결측 데이터 첫날과 마지막날을 index변수에 저장
            first_index = sup[sup['일시'].str.contains(first)].index.values
            end_index = sup[sup['일시'].str.contains(end)].index.values

            # 첫날과 마지막 날짜를 슬라이싱으로 시간만 표시 후 해당 시간이 포함된 날을 first, end 인덱스와 대조해 boolean 리스트 생성
            first_list=sup[sup['일시'].str.contains(first[10:])].reset_index()['index']==first_index[0]
            end_list=sup[sup['일시'].str.contains(end[10:])].reset_index()['index']==end_index[0]

            # boolean 리스트 중 True값의 인덱스를 point 변수로 선언
            for i in range(len(first_list)):
                if first_list[i] == True:
                    first_point = i

            for i in range(len(end_list)):
                if end_list[i] == True:
                    end_point = i

        # 다수의 공백들은 해당시간의 과거 2일동안 평균치로 채워넣는다

            for date in pd.date_range(first, end, freq='H'):
                left = sup[sup['일시'].str.contains(str(date)[10:16])].reset_index()[col][first_point-2:first_point].values.mean()
                left = round(left, 1)
                index = sup[sup['일시'].str.contains(str(date)[:16]) & sup[col].isnull()].index
                print(date, left)
                for a in index:
                    sup[col][a] = left

0
2018-10-29 11:00 0.5M 정시 습도(%)
2018-10-29 12:00 0.5M 정시 습도(%)
2018-10-29 13:00 0.5M 정시 습도(%)
2018-10-29 14:00 0.5M 정시 습도(%)
2018-10-29 15:00 0.5M 정시 습도(%)
2018-10-29 16:00 0.5M 정시 습도(%)
2018-10-29 17:00 0.5M 정시 습도(%)
2018-10-29 18:00 0.5M 정시 습도(%)
2018-10-29 19:00 0.5M 정시 습도(%)
2018-10-29 20:00 0.5M 정시 습도(%)
2018-10-29 21:00 0.5M 정시 습도(%)
2018-10-29 22:00 0.5M 정시 습도(%)
2018-10-29 23:00 0.5M 정시 습도(%)
2018-10-30 00:00 0.5M 정시 습도(%)
2018-10-30 01:00 0.5M 정시 습도(%)
2018-10-30 02:00 0.5M 정시 습도(%)
2018-10-30 03:00 0.5M 정시 습도(%)
2018-10-30 04:00 0.5M 정시 습도(%)
2018-10-30 05:00 0.5M 정시 습도(%)
2018-10-30 06:00 0.5M 정시 습도(%)
2018-10-30 07:00 0.5M 정시 습도(%)
2018-10-30 08:00 0.5M 정시 습도(%)
2018-10-30 09:00 0.5M 정시 습도(%)
2018-10-30 10:00 0.5M 정시 습도(%)
2018-10-30 11:00 0.5M 정시 습도(%)
2018-10-30 12:00 0.5M 정시 습도(%)
2018-10-30 13:00 0.5M 정시 습도(%)
2018-10-30 14:00 0.5M 정시 습도(%)
2018-10-30 15:00 0.5M 정시 습도(%)
2018-10-30 16:00 0.5M 정시 습도(%)
2018-10-30 17:00 0.5M 정시 습도(%)
2018-10-30 18:00 0.5M 정시 습도(%)
2018-1

2018-11-10 07:00 0.5M 정시 습도(%)
2018-11-10 08:00 0.5M 정시 습도(%)
2018-11-10 09:00 0.5M 정시 습도(%)
2018-11-10 10:00 0.5M 정시 습도(%)
2018-11-10 11:00 0.5M 정시 습도(%)
2018-11-10 12:00 0.5M 정시 습도(%)
2018-11-10 13:00 0.5M 정시 습도(%)
2018-11-10 14:00 0.5M 정시 습도(%)
2018-11-10 15:00 0.5M 정시 습도(%)
2018-11-10 16:00 0.5M 정시 습도(%)
2018-11-10 17:00 0.5M 정시 습도(%)
2018-11-10 18:00 0.5M 정시 습도(%)
2018-11-10 19:00 0.5M 정시 습도(%)
2018-11-10 20:00 0.5M 정시 습도(%)
2018-11-10 21:00 0.5M 정시 습도(%)
2018-11-10 22:00 0.5M 정시 습도(%)
2018-11-10 23:00 0.5M 정시 습도(%)
2018-11-11 00:00 0.5M 정시 습도(%)
2018-11-11 01:00 0.5M 정시 습도(%)
2018-11-11 02:00 0.5M 정시 습도(%)
2018-11-11 03:00 0.5M 정시 습도(%)
2018-11-11 04:00 0.5M 정시 습도(%)
2018-11-11 05:00 0.5M 정시 습도(%)
2018-11-11 06:00 0.5M 정시 습도(%)
2018-11-11 07:00 0.5M 정시 습도(%)
2018-11-11 08:00 0.5M 정시 습도(%)
2018-11-11 09:00 0.5M 정시 습도(%)
2018-11-11 10:00 0.5M 정시 습도(%)
2018-11-11 11:00 0.5M 정시 습도(%)
2018-11-11 12:00 0.5M 정시 습도(%)
2018-11-11 13:00 0.5M 정시 습도(%)
2018-11-11 14:00 0.5M 정시 습도(%)
2018-11-

2018-11-24 10:00 0.5M 정시 습도(%)
2018-11-24 11:00 0.5M 정시 습도(%)
2018-11-24 12:00 0.5M 정시 습도(%)
2018-11-24 13:00 0.5M 정시 습도(%)
2018-11-24 14:00 0.5M 정시 습도(%)
2018-11-24 15:00 0.5M 정시 습도(%)
2018-11-24 16:00 0.5M 정시 습도(%)
2018-11-24 17:00 0.5M 정시 습도(%)
2018-11-24 18:00 0.5M 정시 습도(%)
2018-11-24 19:00 0.5M 정시 습도(%)
2018-11-24 20:00 0.5M 정시 습도(%)
2018-11-24 21:00 0.5M 정시 습도(%)
2018-11-24 22:00 0.5M 정시 습도(%)
2018-11-24 23:00 0.5M 정시 습도(%)
2018-11-25 00:00 0.5M 정시 습도(%)
2018-11-25 01:00 0.5M 정시 습도(%)
2018-11-25 02:00 0.5M 정시 습도(%)
2018-11-25 03:00 0.5M 정시 습도(%)
2018-11-25 04:00 0.5M 정시 습도(%)
2018-11-25 05:00 0.5M 정시 습도(%)
2018-11-25 06:00 0.5M 정시 습도(%)
2018-11-25 07:00 0.5M 정시 습도(%)
2018-11-25 08:00 0.5M 정시 습도(%)
2018-11-25 09:00 0.5M 정시 습도(%)
2018-11-25 10:00 0.5M 정시 습도(%)
2018-11-25 11:00 0.5M 정시 습도(%)
2018-11-25 12:00 0.5M 정시 습도(%)
2018-11-25 13:00 0.5M 정시 습도(%)
2018-11-25 14:00 0.5M 정시 습도(%)
2018-11-25 15:00 0.5M 정시 습도(%)
2018-11-25 16:00 0.5M 정시 습도(%)
2018-11-25 17:00 0.5M 정시 습도(%)
2018-11-

2018-12-06 13:00 0.5M 정시 습도(%)
2018-12-06 14:00 0.5M 정시 습도(%)
2018-12-06 15:00 0.5M 정시 습도(%)
2018-12-06 16:00 0.5M 정시 습도(%)
2018-12-06 17:00 0.5M 정시 습도(%)
2018-12-06 18:00 0.5M 정시 습도(%)
2018-12-06 19:00 0.5M 정시 습도(%)
2018-12-06 20:00 0.5M 정시 습도(%)
2018-12-06 21:00 0.5M 정시 습도(%)
2018-12-06 22:00 0.5M 정시 습도(%)
2018-12-06 23:00 0.5M 정시 습도(%)
2018-12-07 00:00 0.5M 정시 습도(%)
2018-12-07 01:00 0.5M 정시 습도(%)
2018-12-07 02:00 0.5M 정시 습도(%)
2018-12-07 03:00 0.5M 정시 습도(%)
2018-12-07 04:00 0.5M 정시 습도(%)
2018-12-07 05:00 0.5M 정시 습도(%)
2018-12-07 06:00 0.5M 정시 습도(%)
2018-12-07 07:00 0.5M 정시 습도(%)
2018-12-07 08:00 0.5M 정시 습도(%)
2018-12-07 09:00 0.5M 정시 습도(%)
2018-12-07 10:00 0.5M 정시 습도(%)
2018-12-07 11:00 0.5M 정시 습도(%)
2018-12-07 12:00 0.5M 정시 습도(%)
2018-12-07 13:00 0.5M 정시 습도(%)
2018-12-07 14:00 0.5M 정시 습도(%)
2018-12-07 15:00 0.5M 정시 습도(%)
2018-12-07 16:00 0.5M 정시 습도(%)
2018-12-07 17:00 0.5M 정시 습도(%)
2018-12-07 18:00 0.5M 정시 습도(%)
2018-12-07 19:00 0.5M 정시 습도(%)
2018-12-07 20:00 0.5M 정시 습도(%)
2018-12-

2018-12-20 06:00 0.5M 정시 습도(%)
2018-12-20 07:00 0.5M 정시 습도(%)
2018-12-20 08:00 0.5M 정시 습도(%)
2018-12-20 09:00 0.5M 정시 습도(%)
2018-12-20 10:00 0.5M 정시 습도(%)
2018-12-20 11:00 0.5M 정시 습도(%)
2018-12-20 12:00 0.5M 정시 습도(%)
2018-12-20 13:00 0.5M 정시 습도(%)
2018-12-20 14:00 0.5M 정시 습도(%)
2018-12-20 15:00 0.5M 정시 습도(%)
2018-12-20 16:00 0.5M 정시 습도(%)
2018-12-20 17:00 0.5M 정시 습도(%)
2018-12-20 18:00 0.5M 정시 습도(%)
2018-12-20 19:00 0.5M 정시 습도(%)
2018-12-20 20:00 0.5M 정시 습도(%)
2018-12-20 21:00 0.5M 정시 습도(%)
2018-12-20 22:00 0.5M 정시 습도(%)
2018-12-20 23:00 0.5M 정시 습도(%)
2018-12-21 00:00 0.5M 정시 습도(%)
2018-12-21 01:00 0.5M 정시 습도(%)
2018-12-21 02:00 0.5M 정시 습도(%)
2018-12-21 03:00 0.5M 정시 습도(%)
2018-12-21 04:00 0.5M 정시 습도(%)
2018-12-21 05:00 0.5M 정시 습도(%)
2018-12-21 06:00 0.5M 정시 습도(%)
2018-12-21 07:00 0.5M 정시 습도(%)
2018-12-21 08:00 0.5M 정시 습도(%)
2018-12-21 09:00 0.5M 정시 습도(%)
2018-12-21 10:00 0.5M 정시 습도(%)
2018-12-21 11:00 0.5M 정시 습도(%)
2018-12-21 12:00 0.5M 정시 습도(%)
2018-12-21 13:00 0.5M 정시 습도(%)
2018-12-

KeyError: 8760

In [ ]:
# 공백 체크
for i in tqdm_notebook(data_col):
    for q in range(len(sup)):
        if sup[i].isnull()[q] == True:
            print(q, i, sup['일시'][q])

In [ ]:
# 강수량과 날짜데이터 가져오기
date_list=[]
rain_list=[]
for i in tqdm_notebook(range(1, 10)):
    url = 'http://apis.data.go.kr/1360000/AsosHourlyInfoService/getWthrDataList?serviceKey={}&numOfRows=999&pageNo={}&dataCd=ASOS&dateCd=HR&stnIds={}&endDt={}&endHh=00&startHh=00&startDt={}'.format(key, i, point, day+10000, day)
    content = requests.get(url).content
    dic = xmltodict.parse(content)
    for q in range(999):
        try: 
            date = dic['response']['body']['items']['item'][q]['tm']
            rain = dic['response']['body']['items']['item'][q]['rn']
            if dic['response']['body']['items']['item'][q]['rn'] is None:
                rain = float(0.0)
            date_list.append(date)
            rain_list.append(rain)
        except:
            pass
date_list=date_list[:-1]
rain_list=rain_list[:-1]

In [ ]:
df_rain=pd.DataFrame({'강수량': rain_list, '일시': date_list})
df_rain

In [430]:
sup['강수량']=rain_list

In [431]:
sup.to_csv('TEST/화순능주/{}.csv'.format(year), encoding='cp949')

In [105]:
# 빈 날짜 확인하기
no_date_list = []
for i in range(len(df_rain)):
    no_date_list.append(df_rain['일시'][i][:10])
    
count={}
for i in no_date_list:
    try: count[i] += 1
    except: count[i]=1
count

{'2015-01-01': 24,
 '2015-01-02': 24,
 '2015-01-03': 24,
 '2015-01-04': 24,
 '2015-01-05': 24,
 '2015-01-06': 24,
 '2015-01-07': 24,
 '2015-01-08': 24,
 '2015-01-09': 24,
 '2015-01-10': 24,
 '2015-01-11': 24,
 '2015-01-12': 24,
 '2015-01-13': 24,
 '2015-01-14': 24,
 '2015-01-15': 24,
 '2015-01-16': 24,
 '2015-01-17': 24,
 '2015-01-18': 24,
 '2015-01-19': 24,
 '2015-01-20': 24,
 '2015-01-21': 24,
 '2015-01-22': 24,
 '2015-01-23': 24,
 '2015-01-24': 24,
 '2015-01-25': 24,
 '2015-01-26': 24,
 '2015-01-27': 24,
 '2015-01-28': 24,
 '2015-01-29': 24,
 '2015-01-30': 24,
 '2015-01-31': 24,
 '2015-02-01': 24,
 '2015-02-02': 24,
 '2015-02-03': 24,
 '2015-02-04': 24,
 '2015-02-05': 24,
 '2015-02-06': 24,
 '2015-02-07': 24,
 '2015-02-08': 24,
 '2015-02-09': 24,
 '2015-02-10': 24,
 '2015-02-11': 24,
 '2015-02-12': 24,
 '2015-02-13': 24,
 '2015-02-14': 24,
 '2015-02-15': 24,
 '2015-02-16': 24,
 '2015-02-17': 24,
 '2015-02-18': 24,
 '2015-02-19': 24,
 '2015-02-20': 24,
 '2015-02-21': 24,
 '2015-02-22

In [177]:
###### 개별
lost_data=[]
col = data_col[7]

for i in range(len(sup)):
    if sup[col].isnull()[i] == True and sup[col].isnull()[i+1] == True and sup[col].isnull()[i+2] == True and sup[col].isnull()[i+3] == True and sup[col].isnull()[i+4] == True:
        print(sup['일시'][i], col)
        lost_data.append(sup['일시'][i])
        lost_data.append(sup['일시'][i+1])
        lost_data.append(sup['일시'][i+2])
        lost_data.append(sup['일시'][i+3])
        lost_data.append(sup['일시'][i+4])

lost_data = sorted(list(set(lost_data)))        

# for i in range(len(lost_data)):
#     if len(lost_data[i][10:]) == 5:
#         lost_data[i] = lost_data[i].split(' ')[0] + ' ' + '0' + lost_data[i].split(' ')[1]
# lost_data = sorted(lost_data)

# for i in range(len(lost_data)):
#     if lost_data[i][10:][1] == '0':
#         lost_data[i] = lost_data[i].split(' ')[0] + ' ' + lost_data[i].split(' ')[1][1:]

lost_index = []
for w in range(len(lost_data) - 1):
    if len(pd.date_range(lost_data[w], lost_data[w+1], freq='H')) != 2:
        print(lost_data[w], i, lost_data[w+1], w+1)
        lost_index.append(w)
        lost_index.append(w+1)
lost_index.insert(0, 0)
lost_index.append(len(lost_data)-1)

# 장기 결측 데이터 시작과 끝
for e in tqdm_notebook(range(0, len(lost_index) -1, 2)):
    first = lost_data[lost_index[e]]
    end = lost_data[lost_index[e+1]]

    # 데이터프레임 날짜에서 결측 데이터 첫날과 마지막날을 index변수에 저장
    first_index = sup[sup['일시'].str.contains(first)].index.values
    end_index = sup[sup['일시'].str.contains(end)].index.values

    # 첫날과 마지막 날짜를 슬라이싱으로 시간만 표시 후 해당 시간이 포함된 날을 first, end 인덱스와 대조해 boolean 리스트 생성
    first_list=sup[sup['일시'].str.contains(first[10:])].reset_index()['index']==first_index[0]
    end_list=sup[sup['일시'].str.contains(end[10:])].reset_index()['index']==end_index[0]

    # boolean 리스트 중 True값의 인덱스를 point 변수로 선언
    for i in range(len(first_list)):
        if first_list[i] == True:
            first_point = i

    for i in range(len(end_list)):
        if end_list[i] == True:
            end_point = i

    # 다수의 공백들은 해당시간의 앞뒤로 3일동안 평균치로 채워넣는다

    for date in pd.date_range(first, end, freq='H'):
        left = sup[sup['일시'].str.contains(str(date)[10:16])].reset_index()[col][first_point-3:first_point].values.mean()
        right= sup[sup['일시'].str.contains(str(date)[10:16])].reset_index()[col][end_point+1:end_point+4].values

        if right[0] == None or right[1] == None or right[2] == None:
            right = left
        else:
            right = sup[sup['일시'].str.contains(str(date)[10:16])].reset_index()[col][end_point+1:end_point+4].values.mean()

        if np.isnan(right) == True:
            right = left
        mean = round((left + right) /2, 1)
        index = sup[sup['일시'].str.contains(str(date)[:16]) & sup[col].isnull()].index
        print(date, mean, left, right)
        for a in index:
            sup[col][a] = mean

2019-01-03 01:00 0.5M 정시 기온(°C)
2019-01-03 02:00 0.5M 정시 기온(°C)
2019-01-03 03:00 0.5M 정시 기온(°C)
2019-01-03 04:00 0.5M 정시 기온(°C)
2019-01-04 01:00 0.5M 정시 기온(°C)
2019-01-04 02:00 0.5M 정시 기온(°C)
2019-01-04 03:00 0.5M 정시 기온(°C)
2019-01-04 04:00 0.5M 정시 기온(°C)
2019-01-03 08:00 8759 2019-01-04 01:00 8


C:\Users\leedo\AppData\Local\Temp\ipykernel_31532\3419753395.py:35: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  for e in tqdm_notebook(range(0, len(lost_index) -1, 2)):


  0%|          | 0/2 [00:00<?, ?it/s]

2019-01-03 01:00:00 nan nan nan
2019-01-03 02:00:00 nan nan nan
2019-01-03 03:00:00 nan nan nan
2019-01-03 04:00:00 nan nan nan
2019-01-03 05:00:00 nan nan nan


C:\Users\leedo\AppData\Local\Temp\ipykernel_31532\3419753395.py:59: RuntimeWarning: Mean of empty slice.
  left = sup[sup['일시'].str.contains(str(date)[10:16])].reset_index()[col][first_point-3:first_point].values.mean()
C:\Users\leedo\miniconda3\lib\site-packages\numpy\core\_methods.py:191: RuntimeWarning: invalid value encountered in longlong_scalars
  ret = ret / rcount
C:\Users\leedo\AppData\Local\Temp\ipykernel_31532\3419753395.py:59: RuntimeWarning: Mean of empty slice.
  left = sup[sup['일시'].str.contains(str(date)[10:16])].reset_index()[col][first_point-3:first_point].values.mean()
C:\Users\leedo\miniconda3\lib\site-packages\numpy\core\_methods.py:191: RuntimeWarning: invalid value encountered in longlong_scalars
  ret = ret / rcount
C:\Users\leedo\AppData\Local\Temp\ipykernel_31532\3419753395.py:59: RuntimeWarning: Mean of empty slice.
  left = sup[sup['일시'].str.contains(str(date)[10:16])].reset_index()[col][first_point-3:first_point].values.mean()
C:\Users\leedo\miniconda3\lib\

2019-01-03 06:00:00 nan nan nan


C:\Users\leedo\AppData\Local\Temp\ipykernel_31532\3419753395.py:59: RuntimeWarning: Mean of empty slice.
  left = sup[sup['일시'].str.contains(str(date)[10:16])].reset_index()[col][first_point-3:first_point].values.mean()
C:\Users\leedo\miniconda3\lib\site-packages\numpy\core\_methods.py:191: RuntimeWarning: invalid value encountered in longlong_scalars
  ret = ret / rcount
C:\Users\leedo\AppData\Local\Temp\ipykernel_31532\3419753395.py:59: RuntimeWarning: Mean of empty slice.
  left = sup[sup['일시'].str.contains(str(date)[10:16])].reset_index()[col][first_point-3:first_point].values.mean()
C:\Users\leedo\miniconda3\lib\site-packages\numpy\core\_methods.py:191: RuntimeWarning: invalid value encountered in longlong_scalars
  ret = ret / rcount


2019-01-03 07:00:00 nan nan nan
2019-01-03 08:00:00 nan nan nan
2019-01-04 01:00:00 nan nan 1.633333333333333
2019-01-04 02:00:00 nan nan 1.5833333333333333
2019-01-04 03:00:00 nan nan 1.4833333333333332
2019-01-04 04:00:00 nan nan 1.4166666666666667
2019-01-04 05:00:00 nan nan 1.1666666666666667
2019-01-04 06:00:00 nan nan 1.1666666666666667
2019-01-04 07:00:00 nan nan 1.1666666666666667
2019-01-04 08:00:00 nan nan 1.5666666666666667
